In [ ]:
# Linking to drive
from google.colab import drive
drive.mount("/content/gdrive")

Mounted at /content/gdrive


In [ ]:
!pip install unbabel-comet

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 64 kB 2.2 MB/s 
     |████████████████████████████████| 9.5 MB 10.8 MB/s 
     |████████████████████████████████| 38.1 MB 1.3 MB/s 
     |████████████████████████████████| 1.2 MB 53.4 MB/s 
     |████████████████████████████████| 4.4 MB 58.1 MB/s 
     |████████████████████████████████| 101 kB 14.5 MB/s 
     |████████████████████████████████| 409 kB 46.6 MB/s 
     |████████████████████████████████| 92 kB 13.5 MB/s 
     |████████████████████████████████| 585 kB 66.1 MB/s 
     |████████████████████████████████| 140 kB 75.0 MB/s 
     |████████████████████████████████| 596 kB 68.5 MB/s 
     |████████████████████████████████| 1.1 MB 59.7 MB/s 
     |████████████████████████████████| 6.6 MB 52.4 MB/s 
     |████████████████████████████████| 86 kB 7.0 MB/s 
     |████████████████████████████████| 94 kB 2.8 MB/s 
     |████████████████████████████████

In [ ]:
from comet import download_model, load_from_checkpoint

In [ ]:
# Loading the drive
import os
os.chdir("/content/gdrive/Shareddrives/Low_Budget_MT")

In [ ]:
# Importing needed libraries for preprocessing and visualization
from my_helpers import split_srctgt, generating_BPE, run_model

import warnings
warnings.filterwarnings('ignore')

In [ ]:
#! pip install torch==1.8.0+cu101 -f https://download.pytorch.org/whl/torch_stable.html
#! git clone https://github.com/joeynmt/joeynmt.git
! cd joeynmt; pip3 install . --use-feature=in-tree-build

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Processing /content/gdrive/Shareddrives/Low_Budget_MT/joeynmt
     |████████████████████████████████| 116 kB 15.2 MB/s 
     |████████████████████████████████| 507 kB 69.3 MB/s 
     |████████████████████████████████| 103 kB 65.9 MB/s 
     |████████████████████████████████| 264 kB 74.9 MB/s 
     |████████████████████████████████| 843 kB 58.4 MB/s 
     |████████████████████████████████| 57 kB 6.3 MB/s 
  Created wheel for joeynmt: filename=joeynmt-1.5.1-py3-none-any.whl size=86509 sha256=69922afa32227e5b3ab37066387f2bd2f3a8e98b4c01080ff5cea9690e038034
  Stored in directory: /tmp/pip-ephem-wheel-cache-jvmxupli/wheels/ec/b0/4e/e15e388dd23d01f1c2b4065e1bb36099e5e22abe4f7147f706
  Created wheel for wrapt: filename=wrapt-1.11.1-cp37-cp37m-linux_x86_64.whl size=68426 sha256=19b38d345251b27ad6bed85ca9d7b2fc70d00f327d1f1574c1f7fb4d45763e1a
  Stored in directory: /root/.cache/pip/wheels/4e/58/9d

In [ ]:
!pip install -U torchtext==0.10.0

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 7.6 MB 15.0 MB/s 
     |████████████████████████████████| 831.4 MB 2.8 kB/s 
  Attempting uninstall: torch
    Found existing installation: torch 1.12.1+cu113
    Uninstalling torch-1.12.1+cu113:
      Successfully uninstalled torch-1.12.1+cu113
  Attempting uninstall: torchtext
    Found existing installation: torchtext 0.13.1
    Uninstalling torchtext-0.13.1:
      Successfully uninstalled torchtext-0.13.1
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
torchvision 0.13.1+cu113 requires torch==1.12.1, but you have torch 1.9.0 which is incompatible.
torchaudio 0.12.1+cu113 requires torch==1.12.1, but you have torch 1.9.0 which is incompatible.


In [ ]:
# Setting language and data file:
import pandas as pd
# 3. COMET
def comet(files, train_file, number):

  data = {}
  l  = []
  for i in files: 
    with open(i, "r") as src_file:
        x = src_file.read().splitlines()
        l.append(len(x))
        data[i] = x
  assert l.count(l[0]) == len(l), 'Check your files'

  df = pd.DataFrame(data)
  df.columns = ['source_sentence','target_sentence','scores']
  df["scores"] = pd.to_numeric(df["scores"])
  df = df.sort_values(by = ['scores'])
  print(df.head(1))

  return df.head(number), df.tail(df.shape[0]-number)

def comet_data_load(datafile, target_language, query, k, iteration):

  path = os.getcwd() 
  data_path = 'data/'+target_language
  train_file = '/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/'+k+'/'+'swtrain.csv'
  fpath = os.path.join(path, data_path,k,query)
  print(path)
  print(data_path)
  print(fpath)

  if iteration== str(2):
    it = str(int(iteration)-1)
    train = pd.read_csv('/content/gdrive/Shareddrives/Low_Budget_MT/data/'+target_language+'/'+k+'/'+target_language+'train.csv')
    print(train.shape)
    t, rem = comet([fpath+'/1/rem.en', fpath+'/1/rem.'+target_language, fpath+'/1/scores'], train_file, 20000)
    print(t.shape, rem.shape)
    train_full = pd.concat([train,t])

    os.chdir(fpath)

    t.to_csv(iteration+'.csv', index=False)
    train_full.to_csv(query+'_train.csv', index=False)
    rem.to_csv(query+'_rem.csv',index=False)

    os.chdir(path)

  else:
    os.chdir(fpath)

    it = str(int(iteration)-1)

    train, rem = comet([fpath+'/'+it+'/rem.en', fpath+'/'+it+'/rem.'+target_language, fpath+'/'+it+'/scores'], train_file, 20000)
    print(train.shape)
    train.to_csv(iteration+'.csv', index=False)
    train.to_csv(query+'_train.csv',index=False, mode='a', header=False)
    rem.to_csv(query+'_rem.csv',index=False)

    os.chdir(path)

In [ ]:
def yhat(rem_file, src, tgt,k,iteration,M):
  path = '/content/gdrive/Shareddrives/Low_Budget_MT/data/'+tgt+'/'+k+'/comet/'+iteration
  df = pd.read_csv(rem_file)
  print(df.shape)

  os.chdir(path)
  print(os.getcwd())

  # Splitting x and y:
  os.environ['src'] = src
  os.environ['tgt']  = tgt
  with open("rem."+src, "w") as src_file, open("rem."+tgt, "w") as trg_file:
      for index, row in df.iterrows():
        src_file.write(row["source_sentence"]+"\n")
        trg_file.write(row["target_sentence"]+"\n")

  # Getting bpe for rem
  os.system(' subword-nmt apply-bpe -c bpe.codes.4000 --vocabulary vocab.$tgt < rem.$tgt > rem.bpe.$tgt')
  os.chdir('/content/gdrive/Shareddrives/Low_Budget_MT')
  print(os.getcwd())

  #translate rem
  os.environ["model_path"] = '/content/gdrive/Shareddrives/Low_Budget_MT/joeynmt/models/'+k+'/'+M+'/config.yaml'
  os.environ["x_path"] = path+'/rem.bpe.'+tgt
  os.environ["yhat_path"] = path+'/yhat.'+src

  os.system('cd joeynmt; python -m joeynmt translate $model_path < $x_path > $yhat_path')


def comet_scoring(rem_file, src, tgt,k,iteration,M):
  path = '/content/gdrive/Shareddrives/Low_Budget_MT/data/'+tgt+'/'+k+'/comet/'+iteration
  print('Starting here')
  with open(path+'/rem.'+src, "r") as x_file, open(path+'/rem.bpe.'+tgt, "r") as y_file, open(path+'/yhat.'+src, "r") as z_file:
    x = x_file.read().splitlines()
    y = y_file.read().splitlines()
    z = z_file.read().splitlines()
    print(len(x),len(y),len(z))

  with open(path+'/rem.'+tgt, "r") as a_file:
    a = a_file.read().splitlines()

    print(len(a))

  f = [i for i,j in enumerate(z) if len(j)==0]

  if len(f) !=0:
    x = [i for j, i in enumerate(x) if j not in f]
    y = [i for j, i in enumerate(y) if j not in f]
    z = [i for j, i in enumerate(z) if j not in f]
    a = [i for j, i in enumerate(a) if j not in f]
    
    print(len(x),len(y),len(z))
  
  with open(path+'/rem.'+src, "w") as x_file, open(path+'/rem.bpe.'+tgt, "w") as y_file, open(path+'/yhat.'+src, "w") as z_file:
    for i in zip(x,y,z):
        x_file.write(i[0]+"\n")
        y_file.write(i[1]+"\n")
        z_file.write(i[2]+"\n")

  with open(path+'/rem.'+tgt, "w") as a_file:
    for i in a:
        a_file.write(i+"\n")

  assert len(x)==len(a)==len(z), "Error in translating"

  data = [{'src':i[0], 'mt':i[1]} for i in zip(x,y)]

  model_path = download_model("wmt21-comet-qe-mqm")
  model = load_from_checkpoint(model_path)

  seg_scores, sys_score = model.predict(data, batch_size=8, gpus=1)

  print(len(seg_scores))

  with open(path+'/scores', "w") as x_file:
    for i in seg_scores:
        x_file.write(str(i)+"\n")

  if os.path.exists(path+'/scores'):
    print('done')
  else:
    print('error')

# Swahili COMET K1

## Iteration 1

### Scoring

In [ ]:
comet_scoring('/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k1/rem.csv','en','sw','k1','1','transformer_reverse_ensw2')

Starting here
40602 40602 40602
40602


wmt21-comet-qe-mqm.tar.gz: 1.72GB [00:45, 37.8MB/s]                            
Extracting /root/.cache/torch/unbabel_comet/wmt21-comet-qe-mqm.tar.gz
Extracted /root/.cache/torch/unbabel_comet/wmt21-comet-qe-mqm.tar.gz
Created a temporary directory at /tmp/tmp7s2az292
Writing /tmp/tmp7s2az292/_remote_module_non_sriptable.py


Downloading:   0%|          | 0.00/4.83M [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/616 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/2.09G [00:00<?, ?B/s]

Some weights of the model checkpoint at xlm-roberta-large were not used when initializing XLMRobertaModel: ['lm_head.dense.weight', 'lm_head.bias', 'lm_head.layer_norm.bias', 'lm_head.layer_norm.weight', 'lm_head.decoder.weight', 'lm_head.dense.bias', 'roberta.pooler.dense.weight', 'roberta.pooler.dense.bias']
- This IS expected if you are initializing XLMRobertaModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing XLMRobertaModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Encoder model frozen.
GPU available: True, used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
Predicting Dat

40602
done


## Iteration 2

In [ ]:
comet_data_load('swtrain.csv', 'sw', 'comet','k1', '2')

/content/gdrive/Shareddrives/Low_Budget_MT
data/sw
/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k1/comet
(30000, 2)
                                         source_sentence  \
24734  1 Any member may by notice duly signed by him ...   

                                         target_sentence    scores  
24734  1 Mwanachama yeyote anaweza kutoa ilani yenye ... -0.016778  
(5000, 3) (35602, 3)


In [ ]:
split_srctgt('/data/sw/k1/comet/comet_train.csv','en', 'sw', 'comet','k1', '2')

(35000, 3)


In [ ]:
generating_BPE('en', 'sw', 'comet', 'k1','2')

### Training $M$

In [ ]:
# Swahili to English
run_model('sw', 'sw','en','transformer_reverse_ensw2_comet','comet','k1','2')
! cd joeynmt; python3 -m joeynmt train configs/k1/transformer_reverse_ensw2_comet.yaml

2022-06-17 11:11:24,617 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-06-17 11:11:24,906 - INFO - joeynmt.data - Loading training data...
2022-06-17 11:11:25,331 - INFO - joeynmt.data - Building vocabulary...
2022-06-17 11:11:25,627 - INFO - joeynmt.data - Loading dev data...
2022-06-17 11:11:25,644 - INFO - joeynmt.data - Loading test data...
2022-06-17 11:11:25,922 - INFO - joeynmt.data - Data loaded.
2022-06-17 11:11:25,922 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-06-17 11:11:26,137 - INFO - joeynmt.model - Enc-dec model built.
2022-06-17 11:11:29,932 - INFO - numexpr.utils - NumExpr defaulting to 2 threads.
2022-06-17 11:11:30,342 - INFO - joeynmt.training - Total params: 12133120
2022-06-17 11:11:33,888 - INFO - joeynmt.helpers -                           cfg.name : transformer_reverse_ensw2_comet
2022-06-17 11:11:33,888 - INFO - joeynmt.helpers -                       cfg.data.src : sw
2022-06-17 11:11:33,888 - INFO - joeynmt.helpers -   

### Scoring

In [ ]:
yhat('/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k1/comet/comet_rem.csv', 'en', 'sw','k1','2','transformer_reverse_ensw2_comet')

(35602, 3)
/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k1/comet/2
/content/gdrive/Shareddrives/Low_Budget_MT


In [ ]:
comet_scoring('/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k1/comet/comet_rem.csv', 'en', 'sw','k1','2','transformer_reverse_ensw2_comet')

Starting here
35602 35602 35602


35602


wmt21-comet-qe-mqm.tar.gz: 1.72GB [02:17, 12.5MB/s]                            
Extracting /root/.cache/torch/unbabel_comet/wmt21-comet-qe-mqm.tar.gz
Extracted /root/.cache/torch/unbabel_comet/wmt21-comet-qe-mqm.tar.gz
Created a temporary directory at /tmp/tmp9wb4zft2
Writing /tmp/tmp9wb4zft2/_remote_module_non_sriptable.py


Downloading:   0%|          | 0.00/4.83M [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/616 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/2.09G [00:00<?, ?B/s]

Some weights of the model checkpoint at xlm-roberta-large were not used when initializing XLMRobertaModel: ['roberta.pooler.dense.weight', 'lm_head.bias', 'roberta.pooler.dense.bias', 'lm_head.layer_norm.bias', 'lm_head.layer_norm.weight', 'lm_head.decoder.weight', 'lm_head.dense.bias', 'lm_head.dense.weight']
- This IS expected if you are initializing XLMRobertaModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing XLMRobertaModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Encoder model frozen.
GPU available: True, used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
Predicting Dat

35602
done


## Iteration 3

In [ ]:
comet_data_load('swtrain.csv', 'sw', 'comet','k1','3')

/content/gdrive/Shareddrives/Low_Budget_MT
data/sw
/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k1/comet
                                       source_sentence  \
947  Forbidden to you are your mothers and your dau...   

                                       target_sentence    scores  
947  Mmeharimishiwa mama zenu, na binti zenu, na da... -0.008419  
(5000, 3)


In [ ]:
split_srctgt('/data/sw/k1/comet/comet_train.csv','en', 'sw', 'comet','k1', '3')

(40000, 3)


In [ ]:
generating_BPE('en', 'sw', 'comet','k1', '3')

### Training $M$

In [ ]:
# Swahili to English
run_model('sw', 'sw','en','transformer_reverse_ensw3_comet','comet','k1','3')
! cd joeynmt; python3 -m joeynmt train configs/k1/transformer_reverse_ensw3_comet.yaml

2022-06-17 14:45:10,684 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-06-17 14:45:11,448 - INFO - joeynmt.data - Loading training data...
2022-06-17 14:45:11,943 - INFO - joeynmt.data - Building vocabulary...
2022-06-17 14:45:12,211 - INFO - joeynmt.data - Loading dev data...
2022-06-17 14:45:12,228 - INFO - joeynmt.data - Loading test data...
2022-06-17 14:45:12,491 - INFO - joeynmt.data - Data loaded.
2022-06-17 14:45:12,491 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-06-17 14:45:12,776 - INFO - joeynmt.model - Enc-dec model built.
2022-06-17 14:45:18,149 - INFO - joeynmt.training - Total params: 12133376
2022-06-17 14:45:21,567 - INFO - joeynmt.helpers -                           cfg.name : transformer_reverse_ensw3_comet
2022-06-17 14:45:21,567 - INFO - joeynmt.helpers -                       cfg.data.src : sw
2022-06-17 14:45:21,568 - INFO - joeynmt.helpers -                       cfg.data.trg : en
2022-06-17 14:45:21,568 - INFO - joeynmt.hel

In [ ]:
yhat('/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k1/comet/comet_rem.csv', 'en', 'sw','k1','3','transformer_reverse_ensw3_comet')

(30602, 3)
/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k1/comet/3
/content/gdrive/Shareddrives/Low_Budget_MT


In [ ]:
comet_scoring('/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k1/comet/comet_rem.csv', 'en', 'sw','k1','3','transformer_reverse_ensw3_comet')

Starting here
30602 30602 30602


30602


wmt21-comet-qe-mqm.tar.gz: 1.72GB [00:45, 37.8MB/s]                            
Extracting /root/.cache/torch/unbabel_comet/wmt21-comet-qe-mqm.tar.gz
Extracted /root/.cache/torch/unbabel_comet/wmt21-comet-qe-mqm.tar.gz
Created a temporary directory at /tmp/tmpfca02vyi
Writing /tmp/tmpfca02vyi/_remote_module_non_sriptable.py


Downloading:   0%|          | 0.00/4.83M [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/616 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/2.09G [00:00<?, ?B/s]

Some weights of the model checkpoint at xlm-roberta-large were not used when initializing XLMRobertaModel: ['lm_head.decoder.weight', 'lm_head.dense.bias', 'roberta.pooler.dense.weight', 'lm_head.bias', 'roberta.pooler.dense.bias', 'lm_head.layer_norm.weight', 'lm_head.dense.weight', 'lm_head.layer_norm.bias']
- This IS expected if you are initializing XLMRobertaModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing XLMRobertaModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Encoder model frozen.
GPU available: True, used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
Predicting Dat

30602
done


## Iteration 4

In [ ]:
comet_data_load('swtrain.csv', 'sw', 'comet','k1', '4')

/content/gdrive/Shareddrives/Low_Budget_MT
data/sw
/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k1/comet
                                        source_sentence  \
1449  For what nation is there so great, that has Go...   

                                        target_sentence    scores  
1449  Kwa maana liko taifa gani kubwa, lililo na Mun...  0.032219  
(5000, 3)


In [ ]:
split_srctgt('/data/sw/k1/comet/comet_train.csv','en', 'sw', 'comet','k1', '4')

(45000, 3)


In [ ]:
generating_BPE('en', 'sw', 'comet', 'k1','4')

### Training $M$

In [ ]:
# Swahili to English
run_model('sw', 'sw','en','transformer_reverse_ensw4_comet','comet','k1','4')
! cd joeynmt; python3 -m joeynmt train configs/k1/transformer_reverse_ensw4_comet.yaml

2022-06-17 18:28:09,186 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-06-17 18:28:09,497 - INFO - joeynmt.data - Loading training data...
2022-06-17 18:28:10,173 - INFO - joeynmt.data - Building vocabulary...
2022-06-17 18:28:10,455 - INFO - joeynmt.data - Loading dev data...
2022-06-17 18:28:10,472 - INFO - joeynmt.data - Loading test data...
2022-06-17 18:28:10,632 - INFO - joeynmt.data - Data loaded.
2022-06-17 18:28:10,633 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-06-17 18:28:11,036 - INFO - joeynmt.model - Enc-dec model built.
2022-06-17 18:28:16,982 - INFO - joeynmt.training - Total params: 12133888
2022-06-17 18:28:20,519 - INFO - joeynmt.helpers -                           cfg.name : transformer_reverse_ensw4_comet
2022-06-17 18:28:20,520 - INFO - joeynmt.helpers -                       cfg.data.src : sw
2022-06-17 18:28:20,520 - INFO - joeynmt.helpers -                       cfg.data.trg : en
2022-06-17 18:28:20,520 - INFO - joeynmt.hel

In [ ]:
# Output our validation accuracy
! cat "joeynmt/models/k1/transformer_reverse_ensw4_comet/validations.txt"

Steps: 600	Loss: 102800.28125	PPL: 99.03297	bleu: 0.16768	LR: 0.00100000	*
Steps: 1200	Loss: 92972.60938	PPL: 63.82400	bleu: 0.61358	LR: 0.00100000	*
Steps: 1800	Loss: 86112.14844	PPL: 46.96713	bleu: 1.13513	LR: 0.00100000	*
Steps: 2400	Loss: 81286.77344	PPL: 37.85414	bleu: 1.38418	LR: 0.00100000	*
Steps: 3000	Loss: 77287.35156	PPL: 31.65688	bleu: 3.58896	LR: 0.00100000	*
Steps: 3600	Loss: 73984.45312	PPL: 27.31147	bleu: 4.52254	LR: 0.00100000	*
Steps: 4200	Loss: 71153.05469	PPL: 24.06445	bleu: 5.67790	LR: 0.00100000	*
Steps: 4800	Loss: 68915.14844	PPL: 21.77353	bleu: 6.63562	LR: 0.00100000	*
Steps: 5400	Loss: 66884.13281	PPL: 19.88376	bleu: 7.26911	LR: 0.00100000	*
Steps: 6000	Loss: 65098.21875	PPL: 18.35804	bleu: 7.81917	LR: 0.00100000	*
Steps: 6600	Loss: 63958.53906	PPL: 17.44619	bleu: 8.08689	LR: 0.00100000	*
Steps: 7200	Loss: 62420.88281	PPL: 16.28727	bleu: 9.67465	LR: 0.00100000	*
Steps: 7800	Loss: 61565.24219	PPL: 15.67605	bleu: 9.49919	LR: 0.00100000	*
Steps: 8400	Loss: 60380.0

In [ ]:
# Reloading configuration file
ckpt_number = 21600
config = run_model('sw', 'sw','en','transformer_reverse_ensw4_comet','comet','k1','4')
reload_config = config.replace(
    f'#load_model: path ', 
    f'load_model: "/content/gdrive/Shareddrives/Low_Budget_MT/joeynmt/models/k1/transformer_reverse_ensw4_comet/{ckpt_number}.ckpt"').replace(
        f'model_dir: "models/k1/transformer_reverse_ensw4_comet"', f'model_dir: "models/k1/transformer_reverse_ensw4_comet_reload"').replace(
        f'epochs: 60', f'epochs: 36')
        
with open("joeynmt/configs/k1/transformer_reverse_ensw4_comet_reload.yaml",'w') as f:
    f.write(reload_config)

In [ ]:
# Train continued
!cd joeynmt; python3 -m joeynmt train configs/k1/transformer_reverse_ensw4_comet_reload.yaml

2022-06-17 19:57:40,067 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-06-17 19:57:40,367 - INFO - joeynmt.data - Loading training data...
2022-06-17 19:57:42,199 - INFO - joeynmt.data - Building vocabulary...
2022-06-17 19:57:42,685 - INFO - joeynmt.data - Loading dev data...
2022-06-17 19:57:43,074 - INFO - joeynmt.data - Loading test data...
2022-06-17 19:57:43,724 - INFO - joeynmt.data - Data loaded.
2022-06-17 19:57:43,724 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-06-17 19:57:43,924 - INFO - joeynmt.model - Enc-dec model built.
2022-06-17 19:57:47,744 - INFO - numexpr.utils - NumExpr defaulting to 2 threads.
2022-06-17 19:57:48,321 - INFO - joeynmt.training - Total params: 12133888
2022-06-17 19:57:51,819 - INFO - joeynmt.training - Loading model from /content/gdrive/Shareddrives/Low_Budget_MT/joeynmt/models/k1/transformer_reverse_ensw4_comet/21600.ckpt
2022-06-17 19:57:53,728 - INFO - joeynmt.helpers -                           cfg.name : t

In [ ]:
yhat('/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k1/comet/comet_rem.csv', 'en', 'sw','k1','4','transformer_reverse_ensw4_comet_reload')

(25602, 3)
/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k1/comet/4
/content/gdrive/Shareddrives/Low_Budget_MT


In [ ]:
comet_scoring('/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k1/comet/comet_rem.csv', 'en', 'sw','k1','4','transformer_reverse_ensw4_comet_reload')

Starting here
25602 25602 25602


25602
25599 25599 25599


wmt21-comet-qe-mqm.tar.gz: 1.72GB [00:43, 39.7MB/s]                            
Extracting /root/.cache/torch/unbabel_comet/wmt21-comet-qe-mqm.tar.gz
Extracted /root/.cache/torch/unbabel_comet/wmt21-comet-qe-mqm.tar.gz
Created a temporary directory at /tmp/tmpmadxcqmn
Writing /tmp/tmpmadxcqmn/_remote_module_non_sriptable.py


Downloading:   0%|          | 0.00/4.83M [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/616 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/2.09G [00:00<?, ?B/s]

Some weights of the model checkpoint at xlm-roberta-large were not used when initializing XLMRobertaModel: ['roberta.pooler.dense.weight', 'lm_head.dense.bias', 'roberta.pooler.dense.bias', 'lm_head.decoder.weight', 'lm_head.bias', 'lm_head.layer_norm.weight', 'lm_head.dense.weight', 'lm_head.layer_norm.bias']
- This IS expected if you are initializing XLMRobertaModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing XLMRobertaModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Encoder model frozen.
GPU available: True, used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
Predicting Dat

25599
done


## Iteration 5

In [ ]:
comet_data_load('swtrain.csv', 'sw', 'comet','k1','5')

/content/gdrive/Shareddrives/Low_Budget_MT
data/sw
/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k1/comet
          source_sentence  target_sentence    scores
5734  haggle over a price  shindania fedha  0.040084
(5000, 3)


In [ ]:
split_srctgt('/data/sw/k1/comet/comet_train.csv','en', 'sw', 'comet','k1', '5')

(50000, 3)


In [ ]:
generating_BPE('en', 'sw', 'comet','k1' ,'5')

### Training $M$

In [ ]:
# Swahili to English
run_model('sw', 'sw','en','transformer_reverse_ensw5_comet','comet','k1','5')
! cd joeynmt; python3 -m joeynmt train configs/k1/transformer_reverse_ensw5_comet.yaml

2022-06-18 06:50:52,308 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-06-18 06:50:52,749 - INFO - joeynmt.data - Loading training data...
2022-06-18 06:50:53,433 - INFO - joeynmt.data - Building vocabulary...
2022-06-18 06:50:53,720 - INFO - joeynmt.data - Loading dev data...
2022-06-18 06:50:53,733 - INFO - joeynmt.data - Loading test data...
2022-06-18 06:50:54,057 - INFO - joeynmt.data - Data loaded.
2022-06-18 06:50:54,058 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-06-18 06:50:54,297 - INFO - joeynmt.model - Enc-dec model built.
2022-06-18 06:51:00,279 - INFO - joeynmt.training - Total params: 12133888
2022-06-18 06:51:03,703 - INFO - joeynmt.helpers -                           cfg.name : transformer_reverse_ensw5_comet
2022-06-18 06:51:03,704 - INFO - joeynmt.helpers -                       cfg.data.src : sw
2022-06-18 06:51:03,704 - INFO - joeynmt.helpers -                       cfg.data.trg : en
2022-06-18 06:51:03,704 - INFO - joeynmt.hel

In [ ]:
yhat('/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k1/comet/comet_rem.csv', 'en', 'sw','k1','5','transformer_reverse_ensw5_comet')

(20599, 3)
/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k1/comet/5
/content/gdrive/Shareddrives/Low_Budget_MT


In [ ]:
comet_scoring('/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k1/comet/comet_rem.csv', 'en', 'sw','k1','5','transformer_reverse_ensw5_comet')

Starting here
20599 20599 20599


20599


wmt21-comet-qe-mqm.tar.gz: 1.72GB [00:37, 46.0MB/s]                            
Extracting /root/.cache/torch/unbabel_comet/wmt21-comet-qe-mqm.tar.gz
Extracted /root/.cache/torch/unbabel_comet/wmt21-comet-qe-mqm.tar.gz
Created a temporary directory at /tmp/tmpa9eoa2yl
Writing /tmp/tmpa9eoa2yl/_remote_module_non_sriptable.py


Downloading:   0%|          | 0.00/4.83M [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/616 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/2.09G [00:00<?, ?B/s]

Some weights of the model checkpoint at xlm-roberta-large were not used when initializing XLMRobertaModel: ['lm_head.dense.bias', 'lm_head.bias', 'lm_head.layer_norm.bias', 'roberta.pooler.dense.weight', 'roberta.pooler.dense.bias', 'lm_head.layer_norm.weight', 'lm_head.decoder.weight', 'lm_head.dense.weight']
- This IS expected if you are initializing XLMRobertaModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing XLMRobertaModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Encoder model frozen.
GPU available: True, used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
Predicting Dat

20599
done


## Iteration 6

In [ ]:
comet_data_load('swtrain.csv', 'sw', 'comet','k1', '6')

/content/gdrive/Shareddrives/Low_Budget_MT
data/sw
/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k1/comet
                          source_sentence                  target_sentence  \
357    can’t hold on to this any longer.    Siwezi shikilia kwa hii tena.    

       scores  
357  0.042645  
(5000, 3)


In [ ]:
split_srctgt('/data/sw/k1/comet/comet_train.csv','en', 'sw', 'comet','k1', '6')

(55000, 3)


In [ ]:
generating_BPE('en', 'sw', 'comet','k1', '6')

In [ ]:
# Swahili to English
run_model('sw', 'sw','en','transformer_reverse_ensw6_comet','comet', 'k1','6')
! cd joeynmt; python3 -m joeynmt train configs/k1/transformer_reverse_ensw6_comet.yaml

2022-06-18 11:22:01,926 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-06-18 11:22:02,208 - INFO - joeynmt.data - Loading training data...
2022-06-18 11:22:02,952 - INFO - joeynmt.data - Building vocabulary...
2022-06-18 11:22:03,260 - INFO - joeynmt.data - Loading dev data...
2022-06-18 11:22:03,278 - INFO - joeynmt.data - Loading test data...
2022-06-18 11:22:03,615 - INFO - joeynmt.data - Data loaded.
2022-06-18 11:22:03,616 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-06-18 11:22:03,844 - INFO - joeynmt.model - Enc-dec model built.
2022-06-18 11:22:09,943 - INFO - joeynmt.training - Total params: 12134144
2022-06-18 11:22:13,445 - INFO - joeynmt.helpers -                           cfg.name : transformer_reverse_ensw6_comet
2022-06-18 11:22:13,445 - INFO - joeynmt.helpers -                       cfg.data.src : sw
2022-06-18 11:22:13,445 - INFO - joeynmt.helpers -                       cfg.data.trg : en
2022-06-18 11:22:13,445 - INFO - joeynmt.hel

In [ ]:
# Output our validation accuracy
! cat "joeynmt/models/k1/transformer_reverse_ensw6_comet/validations.txt"

Steps: 600	Loss: 102784.41406	PPL: 99.12556	bleu: 0.13794	LR: 0.00100000	*
Steps: 1200	Loss: 93535.40625	PPL: 65.54806	bleu: 0.56877	LR: 0.00100000	*
Steps: 1800	Loss: 86023.73438	PPL: 46.84626	bleu: 1.64995	LR: 0.00100000	*
Steps: 2400	Loss: 81209.29688	PPL: 37.77229	bleu: 1.58864	LR: 0.00100000	*
Steps: 3000	Loss: 77128.96094	PPL: 31.47232	bleu: 3.34708	LR: 0.00100000	*
Steps: 3600	Loss: 73548.36719	PPL: 26.81573	bleu: 5.06424	LR: 0.00100000	*
Steps: 4200	Loss: 70753.60938	PPL: 23.66532	bleu: 5.13228	LR: 0.00100000	*
Steps: 4800	Loss: 68648.76562	PPL: 21.53942	bleu: 6.43802	LR: 0.00100000	*
Steps: 5400	Loss: 66502.03906	PPL: 19.56781	bleu: 7.87533	LR: 0.00100000	*
Steps: 6000	Loss: 65004.54688	PPL: 18.30035	bleu: 8.31382	LR: 0.00100000	*
Steps: 6600	Loss: 63475.80469	PPL: 17.09108	bleu: 8.26716	LR: 0.00100000	*
Steps: 7200	Loss: 62286.05078	PPL: 16.20553	bleu: 9.37258	LR: 0.00100000	*
Steps: 7800	Loss: 60937.41406	PPL: 15.25707	bleu: 9.60035	LR: 0.00100000	*
Steps: 8400	Loss: 59721.4

In [ ]:
# Reloading configuration file
ckpt_number = 55800
config = run_model('sw', 'sw','en','transformer_reverse_ensw6_comet','comet','k1','6')
reload_config = config.replace(
    f'#load_model: path ', 
    f'load_model: "/content/gdrive/Shareddrives/Low_Budget_MT/joeynmt/models/k1/transformer_reverse_ensw6_comet/{ckpt_number}.ckpt"').replace(
        f'model_dir: "models/k1/transformer_reverse_ensw6_comet"', f'model_dir: "models/k1/transformer_reverse_ensw6_comet_reload"').replace(
        f'epochs: 60', f'epochs: 9')
        
with open("joeynmt/configs/k1/transformer_reverse_ensw6_comet_reload.yaml",'w') as f:
    f.write(reload_config)

In [ ]:

# Train continued
!cd joeynmt; python3 -m joeynmt train configs/k1/transformer_reverse_ensw6_comet_reload.yaml

2022-06-18 14:45:45,806 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-06-18 14:45:46,157 - INFO - joeynmt.data - Loading training data...
2022-06-18 14:45:49,281 - INFO - joeynmt.data - Building vocabulary...
2022-06-18 14:45:49,815 - INFO - joeynmt.data - Loading dev data...
2022-06-18 14:45:50,333 - INFO - joeynmt.data - Loading test data...
2022-06-18 14:45:51,259 - INFO - joeynmt.data - Data loaded.
2022-06-18 14:45:51,260 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-06-18 14:45:51,459 - INFO - joeynmt.model - Enc-dec model built.
2022-06-18 14:45:56,413 - INFO - numexpr.utils - NumExpr defaulting to 2 threads.
2022-06-18 14:45:57,006 - INFO - joeynmt.training - Total params: 12134144
2022-06-18 14:46:00,549 - INFO - joeynmt.training - Loading model from /content/gdrive/Shareddrives/Low_Budget_MT/joeynmt/models/k1/transformer_reverse_ensw6_comet/55800.ckpt
2022-06-18 14:46:03,384 - INFO - joeynmt.helpers -                           cfg.name : t

# Swahili COMET K2

## Iteration 1

### Scoring

In [ ]:
comet_scoring('/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k2/rem.csv','en','sw','k2','1','transformer_reverse_ensw2')

Starting here
40604 40604 40604


40604


wmt21-comet-qe-mqm.tar.gz: 1.72GB [02:12, 13.0MB/s]                            
Extracting /root/.cache/torch/unbabel_comet/wmt21-comet-qe-mqm.tar.gz
Extracted /root/.cache/torch/unbabel_comet/wmt21-comet-qe-mqm.tar.gz
Created a temporary directory at /tmp/tmp9g99try9
Writing /tmp/tmp9g99try9/_remote_module_non_sriptable.py


Downloading:   0%|          | 0.00/4.83M [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/616 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/2.09G [00:00<?, ?B/s]

Some weights of the model checkpoint at xlm-roberta-large were not used when initializing XLMRobertaModel: ['lm_head.layer_norm.bias', 'lm_head.bias', 'lm_head.dense.weight', 'lm_head.decoder.weight', 'lm_head.layer_norm.weight', 'roberta.pooler.dense.bias', 'roberta.pooler.dense.weight', 'lm_head.dense.bias']
- This IS expected if you are initializing XLMRobertaModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing XLMRobertaModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Encoder model frozen.
GPU available: True, used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
Predicting Dat

40604
done


## Iteration 2

In [ ]:
comet_data_load('swtrain.csv', 'sw', 'comet','k2', '2')

/content/gdrive/Shareddrives/Low_Budget_MT
data/sw
/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k2/comet
(30000, 2)
                                         source_sentence  \
15285  The burden concerning the beasts of the south:...   

                                         target_sentence    scores  
15285  Ufunuo juu ya hayawani wa Negebu. Katikati ya ... -0.009951  
(5000, 3) (35604, 3)


In [ ]:
split_srctgt('/data/sw/k2/comet/comet_train.csv','en', 'sw', 'comet','k2', '2')

(35000, 3)


In [ ]:
generating_BPE('en', 'sw', 'comet', 'k2','2')

### Training $M$

In [ ]:
# Swahili to English
run_model('sw', 'sw','en','transformer_reverse_ensw2_comet','comet','k2','2')
! cd joeynmt; python3 -m joeynmt train configs/k2/transformer_reverse_ensw2_comet.yaml

2022-06-18 16:02:53,643 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-06-18 16:02:54,614 - INFO - joeynmt.data - Loading training data...
2022-06-18 16:02:55,033 - INFO - joeynmt.data - Building vocabulary...
2022-06-18 16:02:55,312 - INFO - joeynmt.data - Loading dev data...
2022-06-18 16:02:55,325 - INFO - joeynmt.data - Loading test data...
2022-06-18 16:02:55,606 - INFO - joeynmt.data - Data loaded.
2022-06-18 16:02:55,606 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-06-18 16:02:55,818 - INFO - joeynmt.model - Enc-dec model built.
2022-06-18 16:03:01,360 - INFO - joeynmt.training - Total params: 12132352
2022-06-18 16:03:04,773 - INFO - joeynmt.helpers -                           cfg.name : transformer_reverse_ensw2_comet
2022-06-18 16:03:04,774 - INFO - joeynmt.helpers -                       cfg.data.src : sw
2022-06-18 16:03:04,774 - INFO - joeynmt.helpers -                       cfg.data.trg : en
2022-06-18 16:03:04,774 - INFO - joeynmt.hel

### Scoring

In [ ]:
yhat('/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k2/comet/comet_rem.csv', 'en', 'sw','k2','2','transformer_reverse_ensw2_comet')

(35604, 3)
/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k2/comet/2
/content/gdrive/Shareddrives/Low_Budget_MT


In [ ]:
comet_scoring('/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k2/comet/comet_rem.csv', 'en', 'sw','k2','2','transformer_reverse_ensw2_comet')

Starting here
35604 35604 35604


35604


wmt21-comet-qe-mqm.tar.gz: 1.72GB [00:33, 51.5MB/s]                            
Extracting /root/.cache/torch/unbabel_comet/wmt21-comet-qe-mqm.tar.gz
Extracted /root/.cache/torch/unbabel_comet/wmt21-comet-qe-mqm.tar.gz
Created a temporary directory at /tmp/tmpdg4feet9
Writing /tmp/tmpdg4feet9/_remote_module_non_sriptable.py


Downloading:   0%|          | 0.00/4.83M [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/616 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/2.09G [00:00<?, ?B/s]

Some weights of the model checkpoint at xlm-roberta-large were not used when initializing XLMRobertaModel: ['lm_head.layer_norm.bias', 'lm_head.bias', 'lm_head.decoder.weight', 'roberta.pooler.dense.weight', 'lm_head.layer_norm.weight', 'lm_head.dense.weight', 'roberta.pooler.dense.bias', 'lm_head.dense.bias']
- This IS expected if you are initializing XLMRobertaModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing XLMRobertaModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Encoder model frozen.
GPU available: True, used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
Predicting Dat

35604
done


## Iteration 3

In [ ]:
comet_data_load('swtrain.csv', 'sw', 'comet','k2','3')

/content/gdrive/Shareddrives/Low_Budget_MT
data/sw
/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k2/comet
                                       source_sentence  \
146  Thus says God the LORD, he that created the he...   

                                       target_sentence    scores  
146  Mungu Bwana anena, yeye aliyeziumba mbingu, na...  0.018831  
(5000, 3)


In [ ]:
split_srctgt('/data/sw/k2/comet/comet_train.csv','en', 'sw', 'comet','k2', '3')

(40000, 3)


In [ ]:
generating_BPE('en', 'sw', 'comet','k2', '3')

### Training $M$

In [ ]:
# Swahili to English
run_model('sw', 'sw','en','transformer_reverse_ensw3_comet','comet','k2','3')
! cd joeynmt; python3 -m joeynmt train configs/k2/transformer_reverse_ensw3_comet.yaml

2022-06-18 19:43:19,512 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-06-18 19:43:19,850 - INFO - joeynmt.data - Loading training data...
2022-06-18 19:43:20,348 - INFO - joeynmt.data - Building vocabulary...
2022-06-18 19:43:20,639 - INFO - joeynmt.data - Loading dev data...
2022-06-18 19:43:20,657 - INFO - joeynmt.data - Loading test data...
2022-06-18 19:43:20,948 - INFO - joeynmt.data - Data loaded.
2022-06-18 19:43:20,949 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-06-18 19:43:21,154 - INFO - joeynmt.model - Enc-dec model built.
2022-06-18 19:43:25,307 - INFO - numexpr.utils - NumExpr defaulting to 2 threads.
2022-06-18 19:43:25,865 - INFO - joeynmt.training - Total params: 12132864
2022-06-18 19:43:29,443 - INFO - joeynmt.helpers -                           cfg.name : transformer_reverse_ensw3_comet
2022-06-18 19:43:29,444 - INFO - joeynmt.helpers -                       cfg.data.src : sw
2022-06-18 19:43:29,444 - INFO - joeynmt.helpers -   

In [ ]:
yhat('/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k2/comet/comet_rem.csv', 'en', 'sw','k2','3','transformer_reverse_ensw3_comet')

(30604, 3)
/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k2/comet/3
/content/gdrive/Shareddrives/Low_Budget_MT


In [ ]:
comet_scoring('/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k2/comet/comet_rem.csv', 'en', 'sw','k2','3','transformer_reverse_ensw3_comet')

Starting here
30604 30604 30604


30604


wmt21-comet-qe-mqm.tar.gz: 1.72GB [00:38, 44.7MB/s]                            
Extracting /root/.cache/torch/unbabel_comet/wmt21-comet-qe-mqm.tar.gz
Extracted /root/.cache/torch/unbabel_comet/wmt21-comet-qe-mqm.tar.gz
Created a temporary directory at /tmp/tmp6yy7rqfn
Writing /tmp/tmp6yy7rqfn/_remote_module_non_sriptable.py


Downloading:   0%|          | 0.00/4.83M [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/616 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/2.09G [00:00<?, ?B/s]

Some weights of the model checkpoint at xlm-roberta-large were not used when initializing XLMRobertaModel: ['lm_head.decoder.weight', 'lm_head.dense.weight', 'lm_head.layer_norm.bias', 'roberta.pooler.dense.bias', 'lm_head.layer_norm.weight', 'lm_head.bias', 'lm_head.dense.bias', 'roberta.pooler.dense.weight']
- This IS expected if you are initializing XLMRobertaModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing XLMRobertaModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Encoder model frozen.
GPU available: True, used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
Predicting Dat

30604
done


## Iteration 4

In [ ]:
comet_data_load('swtrain.csv', 'sw', 'comet','k2', '4')

/content/gdrive/Shareddrives/Low_Budget_MT
data/sw
/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k2/comet
                                        source_sentence  \
4373  This was made possible by the continued succes...   

                                        target_sentence    scores  
4373  Hii iliwezekana kutokana na kuendelea kwa mafa...  0.033648  
(5000, 3)


In [ ]:
split_srctgt('/data/sw/k2/comet/comet_train.csv','en', 'sw', 'comet','k2', '4')

(45000, 3)


In [ ]:
generating_BPE('en', 'sw', 'comet', 'k2','4')

### Training $M$

In [ ]:
# Swahili to English
run_model('sw', 'sw','en','transformer_reverse_ensw4_comet','comet','k2','4')
! cd joeynmt; python3 -m joeynmt train configs/k2/transformer_reverse_ensw4_comet.yaml

2022-06-18 23:23:11,278 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-06-18 23:23:11,722 - INFO - joeynmt.data - Loading training data...
2022-06-18 23:23:12,355 - INFO - joeynmt.data - Building vocabulary...
2022-06-18 23:23:12,630 - INFO - joeynmt.data - Loading dev data...
2022-06-18 23:23:12,646 - INFO - joeynmt.data - Loading test data...
2022-06-18 23:23:12,808 - INFO - joeynmt.data - Data loaded.
2022-06-18 23:23:12,808 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-06-18 23:23:13,201 - INFO - joeynmt.model - Enc-dec model built.
2022-06-18 23:23:19,155 - INFO - joeynmt.training - Total params: 12133120
2022-06-18 23:23:22,597 - INFO - joeynmt.helpers -                           cfg.name : transformer_reverse_ensw4_comet
2022-06-18 23:23:22,597 - INFO - joeynmt.helpers -                       cfg.data.src : sw
2022-06-18 23:23:22,597 - INFO - joeynmt.helpers -                       cfg.data.trg : en
2022-06-18 23:23:22,597 - INFO - joeynmt.hel

In [ ]:
# Output our validation accuracy
! cat "joeynmt/models/k2/transformer_reverse_ensw4_comet/validations.txt"

Steps: 600	Loss: 104017.63281	PPL: 104.05176	bleu: 0.07679	LR: 0.00100000	*
Steps: 1200	Loss: 93618.76562	PPL: 65.40045	bleu: 0.74232	LR: 0.00100000	*
Steps: 1800	Loss: 86343.95312	PPL: 47.26044	bleu: 1.52260	LR: 0.00100000	*
Steps: 2400	Loss: 80980.43750	PPL: 37.19472	bleu: 2.29661	LR: 0.00100000	*
Steps: 3000	Loss: 76775.45312	PPL: 30.82709	bleu: 3.61691	LR: 0.00100000	*
Steps: 3600	Loss: 73377.61719	PPL: 26.48727	bleu: 4.80931	LR: 0.00100000	*
Steps: 4200	Loss: 70861.26562	PPL: 23.67209	bleu: 5.51778	LR: 0.00100000	*
Steps: 4800	Loss: 68681.56250	PPL: 21.47657	bleu: 5.94591	LR: 0.00100000	*
Steps: 5400	Loss: 66911.31250	PPL: 19.84421	bleu: 7.10028	LR: 0.00100000	*
Steps: 6000	Loss: 64986.70312	PPL: 18.20997	bleu: 7.62509	LR: 0.00100000	*
Steps: 6600	Loss: 63828.08203	PPL: 17.29178	bleu: 8.52264	LR: 0.00100000	*
Steps: 7200	Loss: 62310.72656	PPL: 16.15895	bleu: 9.32407	LR: 0.00100000	*
Steps: 7800	Loss: 61253.75781	PPL: 15.41399	bleu: 9.67308	LR: 0.00100000	*
Steps: 8400	Loss: 60455.

In [ ]:
# Reloading configuration file
ckpt_number = 40200
config = run_model('sw', 'sw','en','transformer_reverse_ensw4_comet','comet','k2','4')
reload_config = config.replace(
    f'#load_model: path ', 
    f'load_model: "/content/gdrive/Shareddrives/Low_Budget_MT/joeynmt/models/k2/transformer_reverse_ensw4_comet/{ckpt_number}.ckpt"').replace(
        f'model_dir: "models/k2/transformer_reverse_ensw4_comet"', f'model_dir: "models/k2/transformer_reverse_ensw4_comet_reload"').replace(
        f'epochs: 60', f'epochs: 16')
        
with open("joeynmt/configs/k2/transformer_reverse_ensw4_comet_reload.yaml",'w') as f:
    f.write(reload_config)

In [ ]:
# Train continued
!cd joeynmt; python3 -m joeynmt train configs/k2/transformer_reverse_ensw4_comet_reload.yaml

2022-06-19 07:14:36,159 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-06-19 07:14:36,442 - INFO - joeynmt.data - Loading training data...
2022-06-19 07:14:38,758 - INFO - joeynmt.data - Building vocabulary...
2022-06-19 07:14:39,252 - INFO - joeynmt.data - Loading dev data...
2022-06-19 07:14:39,697 - INFO - joeynmt.data - Loading test data...
2022-06-19 07:14:40,355 - INFO - joeynmt.data - Data loaded.
2022-06-19 07:14:40,355 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-06-19 07:14:40,565 - INFO - joeynmt.model - Enc-dec model built.
2022-06-19 07:14:44,579 - INFO - numexpr.utils - NumExpr defaulting to 2 threads.
2022-06-19 07:14:45,409 - INFO - joeynmt.training - Total params: 12133120
2022-06-19 07:14:48,938 - INFO - joeynmt.training - Loading model from /content/gdrive/Shareddrives/Low_Budget_MT/joeynmt/models/k2/transformer_reverse_ensw4_comet/40200.ckpt
2022-06-19 07:14:50,999 - INFO - joeynmt.helpers -                           cfg.name : t

In [ ]:
yhat('/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k2/comet/comet_rem.csv', 'en', 'sw','k2','4','transformer_reverse_ensw4_comet_reload')

(25604, 3)
/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k2/comet/4
/content/gdrive/Shareddrives/Low_Budget_MT


In [ ]:
comet_scoring('/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k2/comet/comet_rem.csv', 'en', 'sw','k2','4','transformer_reverse_ensw4_comet_reload')

Starting here
25604 25604 25604


25604


wmt21-comet-qe-mqm.tar.gz: 1.72GB [02:10, 13.2MB/s]                            
Extracting /root/.cache/torch/unbabel_comet/wmt21-comet-qe-mqm.tar.gz
Extracted /root/.cache/torch/unbabel_comet/wmt21-comet-qe-mqm.tar.gz
Created a temporary directory at /tmp/tmp2l2boohu
Writing /tmp/tmp2l2boohu/_remote_module_non_sriptable.py


Downloading:   0%|          | 0.00/4.83M [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/616 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/2.09G [00:00<?, ?B/s]

Some weights of the model checkpoint at xlm-roberta-large were not used when initializing XLMRobertaModel: ['roberta.pooler.dense.weight', 'roberta.pooler.dense.bias', 'lm_head.decoder.weight', 'lm_head.layer_norm.weight', 'lm_head.dense.weight', 'lm_head.layer_norm.bias', 'lm_head.dense.bias', 'lm_head.bias']
- This IS expected if you are initializing XLMRobertaModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing XLMRobertaModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Encoder model frozen.
GPU available: True, used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
Predicting Dat

25604
done


## Iteration 5

In [ ]:
comet_data_load('swtrain.csv', 'sw', 'comet','k2','5')

/content/gdrive/Shareddrives/Low_Budget_MT
data/sw
/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k2/comet
                             source_sentence target_sentence    scores
10408  bunch of sugar cane bananas palm leaf          uchane  0.041202
(5000, 3)


In [ ]:
split_srctgt('/data/sw/k2/comet/comet_train.csv','en', 'sw', 'comet','k2', '5')

(50000, 3)


In [ ]:
generating_BPE('en', 'sw', 'comet','k2' ,'5')

### Training $M$

In [ ]:
# Swahili to English
run_model('sw', 'sw','en','transformer_reverse_ensw5_comet','comet','k2','5')
! cd joeynmt; python3 -m joeynmt train configs/k2/transformer_reverse_ensw5_comet.yaml

2022-06-19 10:21:56,656 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-06-19 10:21:58,460 - INFO - joeynmt.data - Loading training data...
2022-06-19 10:21:59,149 - INFO - joeynmt.data - Building vocabulary...
2022-06-19 10:21:59,425 - INFO - joeynmt.data - Loading dev data...
2022-06-19 10:21:59,439 - INFO - joeynmt.data - Loading test data...
2022-06-19 10:21:59,770 - INFO - joeynmt.data - Data loaded.
2022-06-19 10:21:59,770 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-06-19 10:21:59,977 - INFO - joeynmt.model - Enc-dec model built.
2022-06-19 10:22:06,077 - INFO - joeynmt.training - Total params: 12133376
2022-06-19 10:22:09,678 - INFO - joeynmt.helpers -                           cfg.name : transformer_reverse_ensw5_comet
2022-06-19 10:22:09,678 - INFO - joeynmt.helpers -                       cfg.data.src : sw
2022-06-19 10:22:09,678 - INFO - joeynmt.helpers -                       cfg.data.trg : en
2022-06-19 10:22:09,678 - INFO - joeynmt.hel

In [ ]:
# Output our validation accuracy
! cat "joeynmt/models/k2/transformer_reverse_ensw5_comet/validations.txt"

Steps: 600	Loss: 104261.64062	PPL: 104.84264	bleu: 0.11116	LR: 0.00100000	*
Steps: 1200	Loss: 93748.32031	PPL: 65.58357	bleu: 0.74698	LR: 0.00100000	*
Steps: 1800	Loss: 87030.40625	PPL: 48.59653	bleu: 1.26557	LR: 0.00100000	*
Steps: 2400	Loss: 81672.84375	PPL: 38.26294	bleu: 2.78705	LR: 0.00100000	*
Steps: 3000	Loss: 77977.13281	PPL: 32.44572	bleu: 3.28525	LR: 0.00100000	*
Steps: 3600	Loss: 74418.57812	PPL: 27.68180	bleu: 4.23154	LR: 0.00100000	*
Steps: 4200	Loss: 71531.41406	PPL: 24.33563	bleu: 5.70075	LR: 0.00100000	*
Steps: 4800	Loss: 69186.05469	PPL: 21.91749	bleu: 6.69222	LR: 0.00100000	*
Steps: 5400	Loss: 67495.74219	PPL: 20.32513	bleu: 7.39144	LR: 0.00100000	*
Steps: 6000	Loss: 65588.89844	PPL: 18.66722	bleu: 7.85472	LR: 0.00100000	*
Steps: 6600	Loss: 63897.67578	PPL: 17.31030	bleu: 8.86625	LR: 0.00100000	*
Steps: 7200	Loss: 62731.03516	PPL: 16.43220	bleu: 9.32708	LR: 0.00100000	*
Steps: 7800	Loss: 61846.12891	PPL: 15.79599	bleu: 9.35007	LR: 0.00100000	*
Steps: 8400	Loss: 60645.

In [ ]:
# Reloading configuration file
ckpt_number = 54000
config = run_model('sw', 'sw','en','transformer_reverse_ensw5_comet','comet','k2','5')
reload_config = config.replace(
    f'#load_model: path ', 
    f'load_model: "/content/gdrive/Shareddrives/Low_Budget_MT/joeynmt/models/k2/transformer_reverse_ensw5_comet/{ckpt_number}.ckpt"').replace(
        f'model_dir: "models/k2/transformer_reverse_ensw5_comet"', f'model_dir: "models/k2/transformer_reverse_ensw5_comet_reload"').replace(
        f'epochs: 60', f'epochs: 6')
        
with open("joeynmt/configs/k2/transformer_reverse_ensw5_comet_reload.yaml",'w') as f:
    f.write(reload_config)

In [ ]:

# Train continued
!cd joeynmt; python3 -m joeynmt train configs/k2/transformer_reverse_ensw5_comet_reload.yaml

2022-06-19 13:58:36,591 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-06-19 13:58:36,811 - INFO - joeynmt.data - Loading training data...
2022-06-19 13:58:39,909 - INFO - joeynmt.data - Building vocabulary...
2022-06-19 13:58:40,425 - INFO - joeynmt.data - Loading dev data...
2022-06-19 13:58:41,167 - INFO - joeynmt.data - Loading test data...
2022-06-19 13:58:41,992 - INFO - joeynmt.data - Data loaded.
2022-06-19 13:58:41,992 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-06-19 13:58:42,292 - INFO - joeynmt.model - Enc-dec model built.
2022-06-19 13:58:46,684 - INFO - numexpr.utils - NumExpr defaulting to 2 threads.
2022-06-19 13:58:47,427 - INFO - joeynmt.training - Total params: 12133376
2022-06-19 13:58:50,950 - INFO - joeynmt.training - Loading model from /content/gdrive/Shareddrives/Low_Budget_MT/joeynmt/models/k2/transformer_reverse_ensw5_comet/54000.ckpt
2022-06-19 13:58:55,980 - INFO - joeynmt.helpers -                           cfg.name : t

In [ ]:
yhat('/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k2/comet/comet_rem.csv', 'en', 'sw','k2','5','transformer_reverse_ensw5_comet_reload')

(20604, 3)
/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k2/comet/5
/content/gdrive/Shareddrives/Low_Budget_MT


In [ ]:
comet_scoring('/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k2/comet/comet_rem.csv', 'en', 'sw','k2','5','transformer_reverse_ensw5_comet')

Starting here
20604 20604 20604


20604


wmt21-comet-qe-mqm.tar.gz: 1.72GB [00:30, 56.6MB/s]                            
Extracting /root/.cache/torch/unbabel_comet/wmt21-comet-qe-mqm.tar.gz
Extracted /root/.cache/torch/unbabel_comet/wmt21-comet-qe-mqm.tar.gz
Created a temporary directory at /tmp/tmp98t35jva
Writing /tmp/tmp98t35jva/_remote_module_non_sriptable.py


Downloading:   0%|          | 0.00/4.83M [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/616 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/2.09G [00:00<?, ?B/s]

Some weights of the model checkpoint at xlm-roberta-large were not used when initializing XLMRobertaModel: ['lm_head.decoder.weight', 'lm_head.dense.bias', 'lm_head.layer_norm.bias', 'lm_head.layer_norm.weight', 'lm_head.bias', 'roberta.pooler.dense.bias', 'roberta.pooler.dense.weight', 'lm_head.dense.weight']
- This IS expected if you are initializing XLMRobertaModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing XLMRobertaModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Encoder model frozen.
GPU available: True, used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
Predicting Dat

20604
done


## Iteration 6

In [ ]:
comet_data_load('swtrain.csv', 'sw', 'comet','k2', '6')

/content/gdrive/Shareddrives/Low_Budget_MT
data/sw
/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k2/comet
     source_sentence target_sentence    scores
4281  follow blindly    funda kidoto  0.044671
(5000, 3)


In [ ]:
split_srctgt('/data/sw/k2/comet/comet_train.csv','en', 'sw', 'comet','k2', '6')

(55000, 3)


In [ ]:
generating_BPE('en', 'sw', 'comet','k2', '6')

In [ ]:
# Swahili to English
run_model('sw', 'sw','en','transformer_reverse_ensw6_comet','comet', 'k2','6')
! cd joeynmt; python3 -m joeynmt train configs/k2/transformer_reverse_ensw6_comet.yaml

2022-06-19 15:01:47,592 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-06-19 15:01:47,982 - INFO - joeynmt.data - Loading training data...
2022-06-19 15:01:48,728 - INFO - joeynmt.data - Building vocabulary...
2022-06-19 15:01:49,017 - INFO - joeynmt.data - Loading dev data...
2022-06-19 15:01:49,041 - INFO - joeynmt.data - Loading test data...
2022-06-19 15:01:49,379 - INFO - joeynmt.data - Data loaded.
2022-06-19 15:01:49,379 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-06-19 15:01:49,598 - INFO - joeynmt.model - Enc-dec model built.
2022-06-19 15:01:56,063 - INFO - joeynmt.training - Total params: 12134144
2022-06-19 15:01:59,523 - INFO - joeynmt.helpers -                           cfg.name : transformer_reverse_ensw6_comet
2022-06-19 15:01:59,523 - INFO - joeynmt.helpers -                       cfg.data.src : sw
2022-06-19 15:01:59,524 - INFO - joeynmt.helpers -                       cfg.data.trg : en
2022-06-19 15:01:59,524 - INFO - joeynmt.hel

In [ ]:
# Output our validation accuracy
! cat "joeynmt/models/k2/transformer_reverse_ensw6_comet/validations.txt"

Steps: 600	Loss: 103980.06250	PPL: 104.00671	bleu: 0.18271	LR: 0.00100000	*
Steps: 1200	Loss: 93455.26562	PPL: 64.99734	bleu: 0.34233	LR: 0.00100000	*
Steps: 1800	Loss: 86702.52344	PPL: 48.07311	bleu: 1.13525	LR: 0.00100000	*
Steps: 2400	Loss: 81185.89844	PPL: 37.57403	bleu: 1.86791	LR: 0.00100000	*
Steps: 3000	Loss: 77377.29688	PPL: 31.69615	bleu: 3.53281	LR: 0.00100000	*
Steps: 3600	Loss: 74327.46094	PPL: 27.65949	bleu: 4.23439	LR: 0.00100000	*
Steps: 4200	Loss: 71476.85938	PPL: 24.35267	bleu: 5.46064	LR: 0.00100000	*
Steps: 4800	Loss: 69130.53125	PPL: 21.92963	bleu: 6.23194	LR: 0.00100000	*
Steps: 5400	Loss: 67180.50781	PPL: 20.10036	bleu: 7.99334	LR: 0.00100000	*
Steps: 6000	Loss: 65552.19531	PPL: 18.69032	bleu: 8.11559	LR: 0.00100000	*
Steps: 6600	Loss: 63973.00781	PPL: 17.41739	bleu: 8.80661	LR: 0.00100000	*
Steps: 7200	Loss: 62858.92578	PPL: 16.57186	bleu: 9.72557	LR: 0.00100000	*
Steps: 7800	Loss: 61714.31250	PPL: 15.74590	bleu: 9.01365	LR: 0.00100000	*
Steps: 8400	Loss: 60557.

In [ ]:
# Reloading configuration file
ckpt_number = 60000
config = run_model('sw', 'sw','en','transformer_reverse_ensw6_comet','comet','k2','6')
reload_config = config.replace(
    f'#load_model: path ', 
    f'load_model: "/content/gdrive/Shareddrives/Low_Budget_MT/joeynmt/models/k2/transformer_reverse_ensw6_comet/{ckpt_number}.ckpt"').replace(
        f'model_dir: "models/k2/transformer_reverse_ensw6_comet"', f'model_dir: "models/k2/transformer_reverse_ensw6_comet_reload"').replace(
        f'epochs: 60', f'epochs: 5')
        
with open("joeynmt/configs/k2/transformer_reverse_ensw6_comet_reload.yaml",'w') as f:
    f.write(reload_config)

In [ ]:

# Train continued
!cd joeynmt; python3 -m joeynmt train configs/k2/transformer_reverse_ensw6_comet_reload.yaml

2022-06-19 18:46:32,191 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-06-19 18:46:33,157 - INFO - joeynmt.data - Loading training data...
2022-06-19 18:46:39,438 - INFO - joeynmt.data - Building vocabulary...
2022-06-19 18:46:40,549 - INFO - joeynmt.data - Loading dev data...
2022-06-19 18:46:42,200 - INFO - joeynmt.data - Loading test data...
2022-06-19 18:46:45,741 - INFO - joeynmt.data - Data loaded.
2022-06-19 18:46:45,741 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-06-19 18:46:45,945 - INFO - joeynmt.model - Enc-dec model built.
2022-06-19 18:46:49,972 - INFO - numexpr.utils - NumExpr defaulting to 2 threads.
2022-06-19 18:46:50,411 - INFO - joeynmt.training - Total params: 12134144
2022-06-19 18:46:53,922 - INFO - joeynmt.training - Loading model from /content/gdrive/Shareddrives/Low_Budget_MT/joeynmt/models/k2/transformer_reverse_ensw6_comet/60000.ckpt
2022-06-19 18:47:00,544 - INFO - joeynmt.helpers -                           cfg.name : t

# Swahili COMET K3

## Iteration 5

### AL Strategy and preprocessing

In [ ]:
data_load('/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k4/swtrain.csv', 'sw', 'random', 'k4', '2')

/content/gdrive/Shareddrives/Low_Budget_MT
data/sw/k4
/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k4/random
(30000, 2) (40604, 2)


In [ ]:
split_srctgt('/data/sw/k4/random/random_train.csv','en', 'sw', 'random', 'k4', '2')

(50000, 2)


In [ ]:
generating_BPE('en', 'sw', 'random', 'k4', '2')

In [ ]:
# Swahili to English
run_model('sw', 'sw','en','transformer_reverse_ensw2','random', 'k4', '2')
! cd joeynmt; python3 -m joeynmt train configs/k4/transformer_reverse_ensw2.yaml

2022-06-22 07:23:39,199 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-06-22 07:23:39,235 - INFO - joeynmt.data - Loading training data...
2022-06-22 07:23:39,906 - INFO - joeynmt.data - Building vocabulary...
2022-06-22 07:23:40,181 - INFO - joeynmt.data - Loading dev data...
2022-06-22 07:23:40,195 - INFO - joeynmt.data - Loading test data...
2022-06-22 07:23:40,533 - INFO - joeynmt.data - Data loaded.
2022-06-22 07:23:40,533 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-06-22 07:23:40,730 - INFO - joeynmt.model - Enc-dec model built.
2022-06-22 07:23:42,883 - INFO - numexpr.utils - NumExpr defaulting to 2 threads.
2022-06-22 07:23:43,356 - INFO - joeynmt.training - Total params: 12134656
2022-06-22 07:23:46,821 - INFO - joeynmt.helpers -                           cfg.name : transformer_reverse_ensw2
2022-06-22 07:23:46,821 - INFO - joeynmt.helpers -                       cfg.data.src : sw
2022-06-22 07:23:46,821 - INFO - joeynmt.helpers -         

## Iteration 2

In [ ]:
comet_data_load('swtrain.csv', 'sw', 'comet','k3', '2')

/content/gdrive/Shareddrives/Low_Budget_MT
data/sw
/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k3/comet
(30000, 2)
                                         source_sentence  \
10418  Surely your turning of things upside down shal...   

                                         target_sentence    scores  
10418  Ninyi mnapindua mambo; Je! Mfinyanzi ahesabiwe... -0.014467  
(5000, 3) (35603, 3)


In [ ]:
split_srctgt('/data/sw/k3/comet/comet_train.csv','en', 'sw', 'comet','k3', '2')

(35000, 3)


In [ ]:
generating_BPE('en', 'sw', 'comet', 'k3','2')

### Training $M$

In [ ]:
# Swahili to English
run_model('sw', 'sw','en','transformer_reverse_ensw2_comet','comet','k3','2')
! cd joeynmt; python3 -m joeynmt train configs/k3/transformer_reverse_ensw2_comet.yaml

2022-06-29 08:36:39,576 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-06-29 08:36:39,840 - INFO - joeynmt.data - Loading training data...
2022-06-29 08:36:40,270 - INFO - joeynmt.data - Building vocabulary...
2022-06-29 08:36:40,560 - INFO - joeynmt.data - Loading dev data...
2022-06-29 08:36:40,573 - INFO - joeynmt.data - Loading test data...
2022-06-29 08:36:40,867 - INFO - joeynmt.data - Data loaded.
2022-06-29 08:36:40,868 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-06-29 08:36:41,067 - INFO - joeynmt.model - Enc-dec model built.
2022-06-29 08:36:44,918 - INFO - numexpr.utils - NumExpr defaulting to 2 threads.
2022-06-29 08:36:45,402 - INFO - joeynmt.training - Total params: 12131584
2022-06-29 08:36:48,925 - INFO - joeynmt.helpers -                           cfg.name : transformer_reverse_ensw2_comet
2022-06-29 08:36:48,926 - INFO - joeynmt.helpers -                       cfg.data.src : sw
2022-06-29 08:36:48,926 - INFO - joeynmt.helpers -   

## Iteration 3

In [ ]:
comet_data_load('swtrain.csv', 'sw', 'comet','k3', '3')

/content/gdrive/Shareddrives/Low_Budget_MT
data/sw
/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k3/comet
                                       source_sentence  \
328  (2) A regional or county government shall not ...   

                                       target_sentence    scores  
328  (2) serikali ya eneo ama wilaya haitasimamishw...  0.021571  
(5000, 3)


In [ ]:
split_srctgt('/data/sw/k3/comet/comet_train.csv','en', 'sw', 'comet','k3', '3')

(40000, 3)


In [ ]:
generating_BPE('en', 'sw', 'comet', 'k3','3')

### Training $M$

In [ ]:
# Swahili to English
run_model('sw', 'sw','en','transformer_reverse_ensw3_comet','comet','k3','3')
! cd joeynmt; python3 -m joeynmt train configs/k3/transformer_reverse_ensw3_comet.yaml

2022-07-01 09:40:05,242 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-07-01 09:40:05,997 - INFO - joeynmt.data - Loading training data...
2022-07-01 09:40:06,478 - INFO - joeynmt.data - Building vocabulary...
2022-07-01 09:40:06,752 - INFO - joeynmt.data - Loading dev data...
2022-07-01 09:40:06,769 - INFO - joeynmt.data - Loading test data...
2022-07-01 09:40:07,058 - INFO - joeynmt.data - Data loaded.
2022-07-01 09:40:07,058 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-07-01 09:40:07,257 - INFO - joeynmt.model - Enc-dec model built.
2022-07-01 09:40:11,340 - INFO - numexpr.utils - NumExpr defaulting to 2 threads.
2022-07-01 09:40:11,962 - INFO - joeynmt.training - Total params: 12133120
2022-07-01 09:40:15,381 - INFO - joeynmt.helpers -                           cfg.name : transformer_reverse_ensw3_comet
2022-07-01 09:40:15,382 - INFO - joeynmt.helpers -                       cfg.data.src : sw
2022-07-01 09:40:15,382 - INFO - joeynmt.helpers -   

In [ ]:
!cd joeynmt; python -m joeynmt test 'models/k3/transformer_reverse_ensw3_comet/config.yaml'

2022-07-01 21:09:40,462 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-07-01 21:09:40,467 - INFO - joeynmt.data - Building vocabulary...
2022-07-01 21:09:42,968 - INFO - joeynmt.data - Loading dev data...
2022-07-01 21:09:43,676 - INFO - joeynmt.data - Loading test data...
2022-07-01 21:09:44,969 - INFO - joeynmt.data - Data loaded.
2022-07-01 21:09:45,041 - INFO - joeynmt.prediction - Process device: cuda, n_gpu: 1, batch_size per device: 3600
2022-07-01 21:09:45,041 - INFO - joeynmt.prediction - Loading model from models/k3/transformer_reverse_ensw3_comet/48000.ckpt
2022-07-01 21:09:51,102 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-07-01 21:09:51,303 - INFO - joeynmt.model - Enc-dec model built.
2022-07-01 21:09:51,374 - INFO - joeynmt.prediction - Decoding on dev set (/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k3/comet/3/dev.bpe.en)...
2022-07-01 21:10:26,294 - INFO - joeynmt.prediction -  dev bleu[13a]:  28.65 [Beam search decoding wit

## Iteration 4

In [ ]:
comet_data_load('swtrain.csv', 'sw', 'comet','k3', '4')

/content/gdrive/Shareddrives/Low_Budget_MT
data/sw
/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k3/comet
                                        source_sentence  \
3841  For thus says the LORD that created the heaven...   

                                        target_sentence    scores  
3841  Maana Bwana, aliyeziumba mbingu, asema hivi; Y...  0.033375  
(5000, 3)


In [ ]:
split_srctgt('/data/sw/k3/comet/comet_train.csv','en', 'sw', 'comet','k3', '4')

(45000, 3)


In [ ]:
generating_BPE('en', 'sw', 'comet', 'k3','4')

### Training $M$

In [ ]:
# Swahili to English
run_model('sw', 'sw','en','transformer_reverse_ensw4_comet','comet','k3','4')
! cd joeynmt; python3 -m joeynmt train configs/k3/transformer_reverse_ensw4_comet.yaml

2022-07-02 15:15:56,597 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-07-02 15:15:57,106 - INFO - joeynmt.data - Loading training data...
2022-07-02 15:15:57,748 - INFO - joeynmt.data - Building vocabulary...
2022-07-02 15:15:58,053 - INFO - joeynmt.data - Loading dev data...
2022-07-02 15:15:58,067 - INFO - joeynmt.data - Loading test data...
2022-07-02 15:15:58,224 - INFO - joeynmt.data - Data loaded.
2022-07-02 15:15:58,224 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-07-02 15:15:58,425 - INFO - joeynmt.model - Enc-dec model built.
2022-07-02 15:16:02,652 - INFO - numexpr.utils - NumExpr defaulting to 2 threads.
2022-07-02 15:16:03,337 - INFO - joeynmt.training - Total params: 12133120
2022-07-02 15:16:06,891 - INFO - joeynmt.helpers -                           cfg.name : transformer_reverse_ensw4_comet
2022-07-02 15:16:06,892 - INFO - joeynmt.helpers -                       cfg.data.src : sw
2022-07-02 15:16:06,892 - INFO - joeynmt.helpers -   

## Iteration 5

In [ ]:
comet_data_load('swtrain.csv', 'sw', 'comet','k3', '5')

/content/gdrive/Shareddrives/Low_Budget_MT
data/sw
/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k3/comet
                                        source_sentence  \
1700  The strong market growth led to increased conc...   

                                        target_sentence    scores  
1700  Ukuaji mkubwa wa soko umesababisha kuelekeza z...  0.042541  
(5000, 3)


In [ ]:
split_srctgt('/data/sw/k3/comet/comet_train.csv','en', 'sw', 'comet','k3', '5')

(50000, 3)


In [ ]:
generating_BPE('en', 'sw', 'comet', 'k3','5')

### Training $M$

In [ ]:
# Swahili to English
run_model('sw', 'sw','en','transformer_reverse_ensw5_comet','comet','k3','5')
! cd joeynmt; python3 -m joeynmt train configs/k3/transformer_reverse_ensw5_comet.yaml

2022-07-03 18:04:20,003 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-07-03 18:04:20,918 - INFO - joeynmt.data - Loading training data...
2022-07-03 18:04:21,629 - INFO - joeynmt.data - Building vocabulary...
2022-07-03 18:04:21,908 - INFO - joeynmt.data - Loading dev data...
2022-07-03 18:04:21,922 - INFO - joeynmt.data - Loading test data...
2022-07-03 18:04:22,256 - INFO - joeynmt.data - Data loaded.
2022-07-03 18:04:22,256 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-07-03 18:04:22,462 - INFO - joeynmt.model - Enc-dec model built.
2022-07-03 18:04:26,560 - INFO - numexpr.utils - NumExpr defaulting to 2 threads.
2022-07-03 18:04:27,215 - INFO - joeynmt.training - Total params: 12133632
2022-07-03 18:04:30,720 - INFO - joeynmt.helpers -                           cfg.name : transformer_reverse_ensw5_comet
2022-07-03 18:04:30,720 - INFO - joeynmt.helpers -                       cfg.data.src : sw
2022-07-03 18:04:30,720 - INFO - joeynmt.helpers -   

In [ ]:
!cd joeynmt; python -m joeynmt test 'models/k3/transformer_reverse_ensw5_comet/config.yaml'

2022-07-05 22:03:48,752 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-07-05 22:03:50,351 - INFO - joeynmt.data - Building vocabulary...
2022-07-05 22:03:54,693 - INFO - joeynmt.data - Loading dev data...
2022-07-05 22:03:55,994 - INFO - joeynmt.data - Loading test data...
2022-07-05 22:03:57,960 - INFO - joeynmt.data - Data loaded.
2022-07-05 22:03:58,037 - INFO - joeynmt.prediction - Process device: cuda, n_gpu: 1, batch_size per device: 3600
2022-07-05 22:03:58,038 - INFO - joeynmt.prediction - Loading model from models/k3/transformer_reverse_ensw5_comet/58800.ckpt
2022-07-05 22:04:07,220 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-07-05 22:04:07,439 - INFO - joeynmt.model - Enc-dec model built.
2022-07-05 22:04:07,508 - INFO - joeynmt.prediction - Decoding on dev set (/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k3/comet/5/dev.bpe.en)...
2022-07-05 22:04:43,648 - INFO - joeynmt.prediction -  dev bleu[13a]:  30.05 [Beam search decoding wit

## Iteration 6

In [ ]:
comet_data_load('swtrain.csv', 'sw', 'comet','k3', '6')

/content/gdrive/Shareddrives/Low_Budget_MT
data/sw
/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k3/comet
                                        source_sentence  \
1392  If we find an ethical problem it will be discu...   

                                        target_sentence    scores  
1392  Ikiwa tutapata tatizo la kimaadili litajadiliw...  0.045357  
(5000, 3)


In [ ]:
split_srctgt('/data/sw/k3/comet/comet_train.csv','en', 'sw', 'comet','k3', '6')

(55000, 3)


In [ ]:
generating_BPE('en', 'sw', 'comet', 'k3','6')

### Training $M$

In [ ]:
# Swahili to English
run_model('sw', 'sw','en','transformer_reverse_ensw6_comet','comet','k3','6')
! cd joeynmt; python3 -m joeynmt train configs/k3/transformer_reverse_ensw6_comet.yaml

2022-07-06 07:45:38,274 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-07-06 07:45:39,235 - INFO - joeynmt.data - Loading training data...
2022-07-06 07:45:39,947 - INFO - joeynmt.data - Building vocabulary...
2022-07-06 07:45:40,224 - INFO - joeynmt.data - Loading dev data...
2022-07-06 07:45:40,245 - INFO - joeynmt.data - Loading test data...
2022-07-06 07:45:40,596 - INFO - joeynmt.data - Data loaded.
2022-07-06 07:45:40,597 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-07-06 07:45:40,802 - INFO - joeynmt.model - Enc-dec model built.
2022-07-06 07:45:44,962 - INFO - numexpr.utils - NumExpr defaulting to 2 threads.
2022-07-06 07:45:45,556 - INFO - joeynmt.training - Total params: 12134400
2022-07-06 07:45:49,518 - INFO - joeynmt.helpers -                           cfg.name : transformer_reverse_ensw6_comet
2022-07-06 07:45:49,519 - INFO - joeynmt.helpers -                       cfg.data.src : sw
2022-07-06 07:45:49,519 - INFO - joeynmt.helpers -   

# Swahili COMET K4

## Iteration 5

In [ ]:
comet_data_load('swtrain.csv', 'sw', 'comet','k4', '2')

/content/gdrive/Shareddrives/Low_Budget_MT
data/sw
/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k4/comet
(30000, 2)
                                         source_sentence  \
10390  Surely your turning of things upside down shal...   

                                         target_sentence    scores  
10390  Ninyi mnapindua mambo; Je! Mfinyanzi ahesabiwe... -0.014762  
(20000, 3) (20604, 3)


In [ ]:
split_srctgt('/data/sw/k4/comet/comet_train.csv','en', 'sw', 'comet','k4', '2')

(50000, 3)


In [ ]:
generating_BPE('en', 'sw', 'comet', 'k4','2')

### Training $M$

In [ ]:
# Swahili to English
run_model('sw', 'sw','en','transformer_reverse_ensw2_comet','comet','k4','2')
! cd joeynmt; python3 -m joeynmt train configs/k4/transformer_reverse_ensw2_comet.yaml

2022-06-23 07:46:02,625 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-06-23 07:46:02,703 - INFO - joeynmt.data - Loading training data...
2022-06-23 07:46:03,445 - INFO - joeynmt.data - Building vocabulary...
2022-06-23 07:46:03,747 - INFO - joeynmt.data - Loading dev data...
2022-06-23 07:46:03,762 - INFO - joeynmt.data - Loading test data...
2022-06-23 07:46:04,110 - INFO - joeynmt.data - Data loaded.
2022-06-23 07:46:04,111 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-06-23 07:46:04,328 - INFO - joeynmt.model - Enc-dec model built.
2022-06-23 07:46:08,084 - INFO - numexpr.utils - NumExpr defaulting to 2 threads.
2022-06-23 07:46:08,727 - INFO - joeynmt.training - Total params: 12134400
2022-06-23 07:46:12,389 - INFO - joeynmt.helpers -                           cfg.name : transformer_reverse_ensw2_comet
2022-06-23 07:46:12,389 - INFO - joeynmt.helpers -                       cfg.data.src : sw
2022-06-23 07:46:12,389 - INFO - joeynmt.helpers -   

## Iteration 2

In [ ]:
comet_data_load('swtrain.csv', 'sw', 'comet','k4', '2')

/content/gdrive/Shareddrives/Low_Budget_MT
data/sw
/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k4/comet
(30000, 2)
                                         source_sentence  \
10390  Surely your turning of things upside down shal...   

                                         target_sentence    scores  
10390  Ninyi mnapindua mambo; Je! Mfinyanzi ahesabiwe... -0.014762  
(5000, 3) (35604, 3)


In [ ]:
split_srctgt('/data/sw/k4/comet/comet_train.csv','en', 'sw', 'comet','k4', '2')

(35000, 3)


In [ ]:
generating_BPE('en', 'sw', 'comet', 'k4','2')

### Training $M$

In [ ]:
# Swahili to English
run_model('sw', 'sw','en','transformer_reverse_ensw2_comet','comet','k4','2')
! cd joeynmt; python3 -m joeynmt train configs/k4/transformer_reverse_ensw2_comet.yaml

2022-06-29 08:43:03,184 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-06-29 08:43:03,678 - INFO - joeynmt.data - Loading training data...
2022-06-29 08:43:04,092 - INFO - joeynmt.data - Building vocabulary...
2022-06-29 08:43:04,370 - INFO - joeynmt.data - Loading dev data...
2022-06-29 08:43:04,386 - INFO - joeynmt.data - Loading test data...
2022-06-29 08:43:04,679 - INFO - joeynmt.data - Data loaded.
2022-06-29 08:43:04,679 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-06-29 08:43:04,880 - INFO - joeynmt.model - Enc-dec model built.
2022-06-29 08:43:08,426 - INFO - numexpr.utils - NumExpr defaulting to 2 threads.
2022-06-29 08:43:08,850 - INFO - joeynmt.training - Total params: 12132352
2022-06-29 08:43:12,356 - INFO - joeynmt.helpers -                           cfg.name : transformer_reverse_ensw2_comet
2022-06-29 08:43:12,356 - INFO - joeynmt.helpers -                       cfg.data.src : sw
2022-06-29 08:43:12,356 - INFO - joeynmt.helpers -   

## Iteration 3

In [ ]:
comet_data_load('swtrain.csv', 'sw', 'comet','k4', '3')

/content/gdrive/Shareddrives/Low_Budget_MT
data/sw
/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k4/comet
                                       source_sentence  \
977  Members of the management team bring together ...   

                                       target_sentence    scores  
977  Wanachama wa usimamizi hujumuika pamoja kubadi...  0.015579  
(5000, 3)


In [ ]:
split_srctgt('/data/sw/k4/comet/comet_train.csv','en', 'sw', 'comet','k4', '3')

(40000, 3)


In [ ]:
generating_BPE('en', 'sw', 'comet', 'k4','3')

### Training $M$

In [ ]:
# Swahili to English
run_model('sw', 'sw','en','transformer_reverse_ensw3_comet','comet','k4','3')
! cd joeynmt; python3 -m joeynmt train configs/k4/transformer_reverse_ensw3_comet.yaml

2022-07-01 09:47:52,177 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-07-01 09:47:52,528 - INFO - joeynmt.data - Loading training data...
2022-07-01 09:47:53,005 - INFO - joeynmt.data - Building vocabulary...
2022-07-01 09:47:53,293 - INFO - joeynmt.data - Loading dev data...
2022-07-01 09:47:53,314 - INFO - joeynmt.data - Loading test data...
2022-07-01 09:47:53,602 - INFO - joeynmt.data - Data loaded.
2022-07-01 09:47:53,603 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-07-01 09:47:53,813 - INFO - joeynmt.model - Enc-dec model built.
2022-07-01 09:47:57,473 - INFO - numexpr.utils - NumExpr defaulting to 2 threads.
2022-07-01 09:47:58,083 - INFO - joeynmt.training - Total params: 12133120
2022-07-01 09:48:01,621 - INFO - joeynmt.helpers -                           cfg.name : transformer_reverse_ensw3_comet
2022-07-01 09:48:01,621 - INFO - joeynmt.helpers -                       cfg.data.src : sw
2022-07-01 09:48:01,621 - INFO - joeynmt.helpers -   

In [ ]:
# Output our validation accuracy
! cat "joeynmt/models/k4/transformer_reverse_ensw3_comet/validations.txt"

Steps: 600	Loss: 103037.78906	PPL: 99.86372	bleu: 0.14344	LR: 0.00100000	*
Steps: 1200	Loss: 93671.93750	PPL: 65.71540	bleu: 0.52054	LR: 0.00100000	*
Steps: 1800	Loss: 86906.95312	PPL: 48.57304	bleu: 1.54394	LR: 0.00100000	*
Steps: 2400	Loss: 81511.55469	PPL: 38.16802	bleu: 2.22647	LR: 0.00100000	*
Steps: 3000	Loss: 77688.43750	PPL: 32.17463	bleu: 2.99324	LR: 0.00100000	*
Steps: 3600	Loss: 74340.58594	PPL: 27.70447	bleu: 4.47871	LR: 0.00100000	*
Steps: 4200	Loss: 71693.56250	PPL: 24.61418	bleu: 5.01028	LR: 0.00100000	*
Steps: 4800	Loss: 69485.58594	PPL: 22.30183	bleu: 6.30663	LR: 0.00100000	*
Steps: 5400	Loss: 67649.72656	PPL: 20.54548	bleu: 6.89175	LR: 0.00100000	*
Steps: 6000	Loss: 65933.10938	PPL: 19.02856	bleu: 7.79085	LR: 0.00100000	*
Steps: 6600	Loss: 64358.58984	PPL: 17.73590	bleu: 8.29778	LR: 0.00100000	*
Steps: 7200	Loss: 63087.30078	PPL: 16.75653	bleu: 9.34700	LR: 0.00100000	*
Steps: 7800	Loss: 61923.69141	PPL: 15.90761	bleu: 9.34124	LR: 0.00100000	*
Steps: 8400	Loss: 61209.0

In [ ]:
# Reloading configuration file
ckpt_number = 46800
config = run_model('sw', 'sw','en','transformer_reverse_ensw3_comet','comet','k4','3')
reload_config = config.replace(
    f'#load_model: path ', 
    f'load_model: "/content/gdrive/Shareddrives/Low_Budget_MT/joeynmt/models/k4/transformer_reverse_ensw3_comet/{ckpt_number}.ckpt"').replace(
        f'model_dir: "models/k4/transformer_reverse_ensw3_comet"', f'model_dir: "models/k4/transformer_reverse_ensw3_comet_reload"').replace(
        f'epochs: 60', f'epochs: 2')
        
with open("joeynmt/configs/k4/transformer_reverse_ensw3_comet_reload.yaml",'w') as f:
    f.write(reload_config)

In [ ]:
# Train continued
!cd joeynmt; python3 -m joeynmt train configs/k4/transformer_reverse_ensw3_comet_reload.yaml

2022-07-01 21:20:47,140 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-07-01 21:20:47,179 - INFO - joeynmt.data - Loading training data...
2022-07-01 21:20:47,669 - INFO - joeynmt.data - Building vocabulary...
2022-07-01 21:20:47,955 - INFO - joeynmt.data - Loading dev data...
2022-07-01 21:20:47,974 - INFO - joeynmt.data - Loading test data...
2022-07-01 21:20:48,266 - INFO - joeynmt.data - Data loaded.
2022-07-01 21:20:48,266 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-07-01 21:20:48,467 - INFO - joeynmt.model - Enc-dec model built.
2022-07-01 21:20:50,759 - INFO - numexpr.utils - NumExpr defaulting to 2 threads.
2022-07-01 21:20:51,362 - INFO - joeynmt.training - Total params: 12133120
2022-07-01 21:20:54,906 - INFO - joeynmt.training - Loading model from /content/gdrive/Shareddrives/Low_Budget_MT/joeynmt/models/k4/transformer_reverse_ensw3_comet/46800.ckpt
2022-07-01 21:20:56,889 - INFO - joeynmt.helpers -                           cfg.name : t

## Iteration 4

In [ ]:
comet_data_load('swtrain.csv', 'sw', 'comet','k4', '4')

/content/gdrive/Shareddrives/Low_Budget_MT
data/sw
/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k4/comet
                                        source_sentence  \
1267  In recognizing the potential of the business, ...   

                                        target_sentence    scores  
1267  Kwa kutambua uwezo wa biashara, soko limeendel...  0.032043  
(5000, 3)


In [ ]:
split_srctgt('/data/sw/k4/comet/comet_train.csv','en', 'sw', 'comet','k4', '4')

(45000, 3)


In [ ]:
generating_BPE('en', 'sw', 'comet', 'k4','4')

### Training $M$

In [ ]:
# Swahili to English
run_model('sw', 'sw','en','transformer_reverse_ensw4_comet','comet','k4','4')
! cd joeynmt; python3 -m joeynmt train configs/k4/transformer_reverse_ensw4_comet.yaml

2022-07-02 15:18:14,080 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-07-02 15:18:14,887 - INFO - joeynmt.data - Loading training data...
2022-07-02 15:18:15,532 - INFO - joeynmt.data - Building vocabulary...
2022-07-02 15:18:15,816 - INFO - joeynmt.data - Loading dev data...
2022-07-02 15:18:15,829 - INFO - joeynmt.data - Loading test data...
2022-07-02 15:18:15,981 - INFO - joeynmt.data - Data loaded.
2022-07-02 15:18:15,981 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-07-02 15:18:16,190 - INFO - joeynmt.model - Enc-dec model built.
2022-07-02 15:18:19,858 - INFO - numexpr.utils - NumExpr defaulting to 2 threads.
2022-07-02 15:18:20,400 - INFO - joeynmt.training - Total params: 12133888
2022-07-02 15:18:24,005 - INFO - joeynmt.helpers -                           cfg.name : transformer_reverse_ensw4_comet
2022-07-02 15:18:24,005 - INFO - joeynmt.helpers -                       cfg.data.src : sw
2022-07-02 15:18:24,005 - INFO - joeynmt.helpers -   

## Iteration 5

In [ ]:
comet_data_load('swtrain.csv', 'sw', 'comet','k4', '5')

/content/gdrive/Shareddrives/Low_Budget_MT
data/sw
/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k4/comet
                                         source_sentence  \
10390  Therefore shall a man leave his father and his...   

                                         target_sentence    scores  
10390  Kwa hiyo mwanamume atamwacha baba yake na mama...  0.038239  
(5000, 3)


In [ ]:
split_srctgt('/data/sw/k4/comet/comet_train.csv','en', 'sw', 'comet','k4', '5')

(50000, 3)


In [ ]:
generating_BPE('en', 'sw', 'comet', 'k4','5')

### Training $M$

In [ ]:
# Swahili to English
run_model('sw', 'sw','en','transformer_reverse_ensw5_comet','comet','k4','5')
! cd joeynmt; python3 -m joeynmt train configs/k4/transformer_reverse_ensw5_comet.yaml

2022-07-03 18:05:15,064 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-07-03 18:05:16,040 - INFO - joeynmt.data - Loading training data...
2022-07-03 18:05:16,774 - INFO - joeynmt.data - Building vocabulary...
2022-07-03 18:05:17,057 - INFO - joeynmt.data - Loading dev data...
2022-07-03 18:05:17,074 - INFO - joeynmt.data - Loading test data...
2022-07-03 18:05:17,412 - INFO - joeynmt.data - Data loaded.
2022-07-03 18:05:17,412 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-07-03 18:05:17,607 - INFO - joeynmt.model - Enc-dec model built.
2022-07-03 18:05:21,157 - INFO - numexpr.utils - NumExpr defaulting to 2 threads.
2022-07-03 18:05:21,752 - INFO - joeynmt.training - Total params: 12134400
2022-07-03 18:05:25,138 - INFO - joeynmt.helpers -                           cfg.name : transformer_reverse_ensw5_comet
2022-07-03 18:05:25,138 - INFO - joeynmt.helpers -                       cfg.data.src : sw
2022-07-03 18:05:25,138 - INFO - joeynmt.helpers -   

In [ ]:
!cd joeynmt; python -m joeynmt test 'models/k4/transformer_reverse_ensw5_comet/config.yaml'

2022-07-05 22:04:08,158 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-07-05 22:04:09,742 - INFO - joeynmt.data - Building vocabulary...
2022-07-05 22:04:13,983 - INFO - joeynmt.data - Loading dev data...
2022-07-05 22:04:15,447 - INFO - joeynmt.data - Loading test data...
2022-07-05 22:04:17,489 - INFO - joeynmt.data - Data loaded.
2022-07-05 22:04:17,558 - INFO - joeynmt.prediction - Process device: cuda, n_gpu: 1, batch_size per device: 3600
2022-07-05 22:04:17,559 - INFO - joeynmt.prediction - Loading model from models/k4/transformer_reverse_ensw5_comet/58800.ckpt
2022-07-05 22:04:25,574 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-07-05 22:04:25,782 - INFO - joeynmt.model - Enc-dec model built.
2022-07-05 22:04:25,849 - INFO - joeynmt.prediction - Decoding on dev set (/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k4/comet/5/dev.bpe.en)...
2022-07-05 22:05:00,052 - INFO - joeynmt.prediction -  dev bleu[13a]:  30.42 [Beam search decoding wit

## Iteration 6

In [ ]:
comet_data_load('swtrain.csv', 'sw', 'comet','k4', '6')

/content/gdrive/Shareddrives/Low_Budget_MT
data/sw
/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k4/comet
                                        source_sentence  \
2588  (a) be qualified and experienced in economic a...   

                                        target_sentence   scores  
2588  (a) wawe wamefuzu na wana ujuzi katika masuala...  0.04228  
(5000, 3)


In [ ]:
split_srctgt('/data/sw/k4/comet/comet_train.csv','en', 'sw', 'comet','k4', '6')

(55000, 3)


In [ ]:
generating_BPE('en', 'sw', 'comet', 'k4','6')

### Training $M$

In [ ]:
# Swahili to English
run_model('sw', 'sw','en','transformer_reverse_ensw6_comet','comet','k4','6')
! cd joeynmt; python3 -m joeynmt train configs/k4/transformer_reverse_ensw6_comet.yaml

2022-07-06 07:45:40,979 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-07-06 07:45:41,696 - INFO - joeynmt.data - Loading training data...
2022-07-06 07:45:42,450 - INFO - joeynmt.data - Building vocabulary...
2022-07-06 07:45:42,727 - INFO - joeynmt.data - Loading dev data...
2022-07-06 07:45:42,750 - INFO - joeynmt.data - Loading test data...
2022-07-06 07:45:43,078 - INFO - joeynmt.data - Data loaded.
2022-07-06 07:45:43,079 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-07-06 07:45:43,294 - INFO - joeynmt.model - Enc-dec model built.
2022-07-06 07:45:47,307 - INFO - numexpr.utils - NumExpr defaulting to 2 threads.
2022-07-06 07:45:47,693 - INFO - joeynmt.training - Total params: 12135424
2022-07-06 07:45:51,932 - INFO - joeynmt.helpers -                           cfg.name : transformer_reverse_ensw6_comet
2022-07-06 07:45:51,933 - INFO - joeynmt.helpers -                       cfg.data.src : sw
2022-07-06 07:45:51,933 - INFO - joeynmt.helpers -   

# Swahili COMET K5

## Iteration 5

In [ ]:
comet_data_load('swtrain.csv', 'sw', 'comet','k5', '2')

/content/gdrive/Shareddrives/Low_Budget_MT
data/sw
/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k5/comet
(30000, 2)
                                         source_sentence  \
10305  Surely your turning of things upside down shal...   

                                         target_sentence    scores  
10305  Ninyi mnapindua mambo; Je! Mfinyanzi ahesabiwe... -0.014514  
(20000, 3) (20604, 3)


In [ ]:
split_srctgt('/data/sw/k5/comet/comet_train.csv','en', 'sw', 'comet','k5', '2')

(50000, 3)


In [ ]:
generating_BPE('en', 'sw', 'comet', 'k5','2')

### Training $M$

In [ ]:
# Swahili to English
run_model('sw', 'sw','en','transformer_reverse_ensw2_comet','comet','k5','2')
! cd joeynmt; python3 -m joeynmt train configs/k5/transformer_reverse_ensw2_comet.yaml

2022-06-23 07:45:57,804 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-06-23 07:45:58,090 - INFO - joeynmt.data - Loading training data...
2022-06-23 07:45:58,870 - INFO - joeynmt.data - Building vocabulary...
2022-06-23 07:45:59,192 - INFO - joeynmt.data - Loading dev data...
2022-06-23 07:45:59,207 - INFO - joeynmt.data - Loading test data...
2022-06-23 07:45:59,623 - INFO - joeynmt.data - Data loaded.
2022-06-23 07:45:59,623 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-06-23 07:45:59,853 - INFO - joeynmt.model - Enc-dec model built.
2022-06-23 07:46:03,876 - INFO - numexpr.utils - NumExpr defaulting to 2 threads.
2022-06-23 07:46:04,571 - INFO - joeynmt.training - Total params: 12133376
2022-06-23 07:46:08,511 - INFO - joeynmt.helpers -                           cfg.name : transformer_reverse_ensw2_comet
2022-06-23 07:46:08,511 - INFO - joeynmt.helpers -                       cfg.data.src : sw
2022-06-23 07:46:08,511 - INFO - joeynmt.helpers -   

In [ ]:
# Output our validation accuracy
! cat "joeynmt/models/k5/transformer_reverse_ensw2_comet/validations.txt"

Steps: 600	Loss: 103286.05469	PPL: 106.02332	bleu: 0.04939	LR: 0.00100000	*
Steps: 1200	Loss: 93483.45312	PPL: 68.10452	bleu: 0.39216	LR: 0.00100000	*
Steps: 1800	Loss: 86546.40625	PPL: 49.79012	bleu: 0.86245	LR: 0.00100000	*
Steps: 2400	Loss: 81750.38281	PPL: 40.09542	bleu: 1.10018	LR: 0.00100000	*
Steps: 3000	Loss: 78149.13281	PPL: 34.07812	bleu: 1.75623	LR: 0.00100000	*
Steps: 3600	Loss: 75429.52344	PPL: 30.14013	bleu: 3.25788	LR: 0.00100000	*
Steps: 4200	Loss: 72894.01562	PPL: 26.87972	bleu: 3.96402	LR: 0.00100000	*
Steps: 4800	Loss: 70489.08594	PPL: 24.11376	bleu: 4.03801	LR: 0.00100000	*
Steps: 5400	Loss: 69049.22656	PPL: 22.59591	bleu: 4.89283	LR: 0.00100000	*
Steps: 6000	Loss: 67222.69531	PPL: 20.80713	bleu: 5.59599	LR: 0.00100000	*
Steps: 6600	Loss: 65682.31250	PPL: 19.40912	bleu: 6.49632	LR: 0.00100000	*
Steps: 7200	Loss: 64640.44531	PPL: 18.51720	bleu: 7.51181	LR: 0.00100000	*
Steps: 7800	Loss: 63110.15234	PPL: 17.28091	bleu: 7.12519	LR: 0.00100000	*
Steps: 8400	Loss: 62196.

In [ ]:
# Reloading configuration file
ckpt_number = 57600
config = run_model('sw', 'sw','en','transformer_reverse_ensw2_comet','comet','k5','2')
reload_config = config.replace(
    f'#load_model: path ', 
    f'load_model: "/content/gdrive/Shareddrives/Low_Budget_MT/joeynmt/models/k5/transformer_reverse_ensw2_comet/{ckpt_number}.ckpt"').replace(
        f'model_dir: "models/k5/transformer_reverse_ensw2_comet"', f'model_dir: "models/k5/transformer_reverse_ensw2_comet_reload"').replace(
        f'epochs: 60', f'epochs: 2')
        
with open("joeynmt/configs/k5/transformer_reverse_ensw2_comet_reload.yaml",'w') as f:
    f.write(reload_config)

In [ ]:

# Train continued
!cd joeynmt; python3 -m joeynmt train configs/k5/transformer_reverse_ensw2_comet_reload.yaml

2022-06-23 11:51:20,412 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-06-23 11:51:20,767 - INFO - joeynmt.data - Loading training data...
2022-06-23 11:51:24,005 - INFO - joeynmt.data - Building vocabulary...
2022-06-23 11:51:24,562 - INFO - joeynmt.data - Loading dev data...
2022-06-23 11:51:25,134 - INFO - joeynmt.data - Loading test data...
2022-06-23 11:51:26,038 - INFO - joeynmt.data - Data loaded.
2022-06-23 11:51:26,038 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-06-23 11:51:26,238 - INFO - joeynmt.model - Enc-dec model built.
2022-06-23 11:51:30,133 - INFO - numexpr.utils - NumExpr defaulting to 2 threads.
2022-06-23 11:51:30,857 - INFO - joeynmt.training - Total params: 12133376
2022-06-23 11:51:34,396 - INFO - joeynmt.training - Loading model from /content/gdrive/Shareddrives/Low_Budget_MT/joeynmt/models/k5/transformer_reverse_ensw2_comet/57600.ckpt
2022-06-23 11:51:38,060 - INFO - joeynmt.helpers -                           cfg.name : t

In [ ]:
!cd joeynmt; python -m joeynmt test 'models/k4/transformer_reverse_ensw2_comet/config.yaml'

2022-06-23 12:09:13,934 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-06-23 12:09:14,408 - INFO - joeynmt.data - Building vocabulary...
2022-06-23 12:09:15,869 - INFO - joeynmt.data - Loading dev data...
2022-06-23 12:09:16,709 - INFO - joeynmt.data - Loading test data...
2022-06-23 12:09:18,110 - INFO - joeynmt.data - Data loaded.
2022-06-23 12:09:18,143 - INFO - joeynmt.prediction - Process device: cuda, n_gpu: 1, batch_size per device: 3600
2022-06-23 12:09:18,143 - INFO - joeynmt.prediction - Loading model from models/k4/transformer_reverse_ensw2_comet/58800.ckpt
2022-06-23 12:09:26,910 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-06-23 12:09:27,118 - INFO - joeynmt.model - Enc-dec model built.
2022-06-23 12:09:27,184 - INFO - joeynmt.prediction - Decoding on dev set (/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k4/comet/2/dev.bpe.en)...
2022-06-23 12:10:00,726 - INFO - joeynmt.prediction -  dev bleu[13a]:  31.24 [Beam search decoding wit

In [ ]:
!cd joeynmt; python -m joeynmt test 'models/k5/transformer_reverse_ensw2_comet_reload/config.yaml'

2022-06-23 12:20:52,836 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-06-23 12:20:52,840 - INFO - joeynmt.data - Building vocabulary...
2022-06-23 12:20:53,115 - INFO - joeynmt.data - Loading dev data...
2022-06-23 12:20:53,126 - INFO - joeynmt.data - Loading test data...
2022-06-23 12:20:53,290 - INFO - joeynmt.data - Data loaded.
2022-06-23 12:20:53,322 - INFO - joeynmt.prediction - Process device: cuda, n_gpu: 1, batch_size per device: 3600
2022-06-23 12:20:53,322 - INFO - joeynmt.prediction - Loading model from models/k5/transformer_reverse_ensw2_comet_reload/latest.ckpt
2022-06-23 12:20:57,092 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-06-23 12:20:57,291 - INFO - joeynmt.model - Enc-dec model built.
2022-06-23 12:20:57,358 - INFO - joeynmt.prediction - Decoding on dev set (/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k5/comet/2/dev.bpe.en)...
2022-06-23 12:21:34,378 - INFO - joeynmt.prediction -  dev bleu[13a]:  26.43 [Beam search deco

In [ ]:
!cd joeynmt; python -m joeynmt test 'models/k3/transformer_reverse_ensw2_comet/config.yaml'

2022-06-23 12:33:05,372 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-06-23 12:33:05,776 - INFO - joeynmt.data - Building vocabulary...
2022-06-23 12:33:07,573 - INFO - joeynmt.data - Loading dev data...
2022-06-23 12:33:08,324 - INFO - joeynmt.data - Loading test data...
2022-06-23 12:33:09,362 - INFO - joeynmt.data - Data loaded.
2022-06-23 12:33:09,399 - INFO - joeynmt.prediction - Process device: cuda, n_gpu: 1, batch_size per device: 3600
2022-06-23 12:33:09,399 - INFO - joeynmt.prediction - Loading model from models/k3/transformer_reverse_ensw2_comet/58800.ckpt
2022-06-23 12:33:16,840 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-06-23 12:33:17,043 - INFO - joeynmt.model - Enc-dec model built.
2022-06-23 12:33:17,112 - INFO - joeynmt.prediction - Decoding on dev set (/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k3/comet/2/dev.bpe.en)...
2022-06-23 12:33:51,303 - INFO - joeynmt.prediction -  dev bleu[13a]:  30.56 [Beam search decoding wit

## Iteration 2

In [ ]:
comet_data_load('swtrain.csv', 'sw', 'comet','k5', '2')

/content/gdrive/Shareddrives/Low_Budget_MT
data/sw
/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k5/comet
(30000, 2)
                                         source_sentence  \
10305  Surely your turning of things upside down shal...   

                                         target_sentence    scores  
10305  Ninyi mnapindua mambo; Je! Mfinyanzi ahesabiwe... -0.014514  
(5000, 3) (35604, 3)


In [ ]:
split_srctgt('/data/sw/k5/comet/comet_train.csv','en', 'sw', 'comet','k5', '2')

(35000, 3)


In [ ]:
generating_BPE('en', 'sw', 'comet', 'k5','2')

### Training $M$

In [ ]:
# Swahili to English
run_model('sw', 'sw','en','transformer_reverse_ensw2_comet','comet','k5','2')
! cd joeynmt; python3 -m joeynmt train configs/k5/transformer_reverse_ensw2_comet.yaml

2022-06-29 08:46:04,681 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-06-29 08:46:05,031 - INFO - joeynmt.data - Loading training data...
2022-06-29 08:46:05,457 - INFO - joeynmt.data - Building vocabulary...
2022-06-29 08:46:05,758 - INFO - joeynmt.data - Loading dev data...
2022-06-29 08:46:05,770 - INFO - joeynmt.data - Loading test data...
2022-06-29 08:46:06,072 - INFO - joeynmt.data - Data loaded.
2022-06-29 08:46:06,072 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-06-29 08:46:06,274 - INFO - joeynmt.model - Enc-dec model built.
2022-06-29 08:46:10,167 - INFO - numexpr.utils - NumExpr defaulting to 2 threads.
2022-06-29 08:46:10,659 - INFO - joeynmt.training - Total params: 12131072
2022-06-29 08:46:14,234 - INFO - joeynmt.helpers -                           cfg.name : transformer_reverse_ensw2_comet
2022-06-29 08:46:14,234 - INFO - joeynmt.helpers -                       cfg.data.src : sw
2022-06-29 08:46:14,235 - INFO - joeynmt.helpers -   

## Iteration 3

In [ ]:
comet_data_load('swtrain.csv', 'sw', 'comet','k5', '3')

/content/gdrive/Shareddrives/Low_Budget_MT
data/sw
/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k5/comet
                                       source_sentence  \
137  Thus says God the LORD, he that created the he...   

                                       target_sentence    scores  
137  Mungu Bwana anena, yeye aliyeziumba mbingu, na...  0.018762  
(5000, 3)


In [ ]:
split_srctgt('/data/sw/k5/comet/comet_train.csv','en', 'sw', 'comet','k5', '3')

(40000, 3)


In [ ]:
generating_BPE('en', 'sw', 'comet', 'k5','3')

### Training $M$

In [ ]:
# Swahili to English
run_model('sw', 'sw','en','transformer_reverse_ensw3_comet','comet','k5','3')
! cd joeynmt; python3 -m joeynmt train configs/k5/transformer_reverse_ensw3_comet.yaml

2022-07-01 09:54:43,610 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-07-01 09:54:44,043 - INFO - joeynmt.data - Loading training data...
2022-07-01 09:54:44,552 - INFO - joeynmt.data - Building vocabulary...
2022-07-01 09:54:44,847 - INFO - joeynmt.data - Loading dev data...
2022-07-01 09:54:44,869 - INFO - joeynmt.data - Loading test data...
2022-07-01 09:54:45,178 - INFO - joeynmt.data - Data loaded.
2022-07-01 09:54:45,184 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-07-01 09:54:45,403 - INFO - joeynmt.model - Enc-dec model built.
2022-07-01 09:54:49,411 - INFO - numexpr.utils - NumExpr defaulting to 2 threads.
2022-07-01 09:54:50,138 - INFO - joeynmt.training - Total params: 12132096
2022-07-01 09:54:53,867 - INFO - joeynmt.helpers -                           cfg.name : transformer_reverse_ensw3_comet
2022-07-01 09:54:53,868 - INFO - joeynmt.helpers -                       cfg.data.src : sw
2022-07-01 09:54:53,868 - INFO - joeynmt.helpers -   

In [ ]:
# Output our validation accuracy
! cat "joeynmt/models/k5/transformer_reverse_ensw3_comet/validations.txt"

Steps: 600	Loss: 102765.67188	PPL: 103.40943	bleu: 0.07925	LR: 0.00100000	*
Steps: 1200	Loss: 93585.23438	PPL: 68.32694	bleu: 0.50000	LR: 0.00100000	*
Steps: 1800	Loss: 86796.07812	PPL: 50.29226	bleu: 0.79436	LR: 0.00100000	*
Steps: 2400	Loss: 82033.80469	PPL: 40.56432	bleu: 1.29270	LR: 0.00100000	*
Steps: 3000	Loss: 77968.55469	PPL: 33.76381	bleu: 2.49110	LR: 0.00100000	*
Steps: 3600	Loss: 74956.96875	PPL: 29.47230	bleu: 3.84427	LR: 0.00100000	*
Steps: 4200	Loss: 72460.63281	PPL: 26.33160	bleu: 4.13821	LR: 0.00100000	*
Steps: 4800	Loss: 69919.08594	PPL: 23.47762	bleu: 5.20110	LR: 0.00100000	*
Steps: 5400	Loss: 68133.21875	PPL: 21.65933	bleu: 6.29479	LR: 0.00100000	*
Steps: 6000	Loss: 66667.47656	PPL: 20.27270	bleu: 6.19590	LR: 0.00100000	*
Steps: 6600	Loss: 65100.06250	PPL: 18.88795	bleu: 7.29863	LR: 0.00100000	*
Steps: 7200	Loss: 63941.66797	PPL: 17.92570	bleu: 6.85626	LR: 0.00100000	*
Steps: 7800	Loss: 62351.50391	PPL: 16.68413	bleu: 8.62807	LR: 0.00100000	*
Steps: 8400	Loss: 61519.

In [ ]:
# Reloading configuration file
ckpt_number = 45000
config = run_model('sw', 'sw','en','transformer_reverse_ensw3_comet','comet','k5','3')
reload_config = config.replace(
    f'#load_model: path ', 
    f'load_model: "/content/gdrive/Shareddrives/Low_Budget_MT/joeynmt/models/k5/transformer_reverse_ensw3_comet/{ckpt_number}.ckpt"').replace(
        f'model_dir: "models/k5/transformer_reverse_ensw3_comet"', f'model_dir: "models/k5/transformer_reverse_ensw3_comet_reload"').replace(
        f'epochs: 60', f'epochs: 4')
        
with open("joeynmt/configs/k5/transformer_reverse_ensw3_comet_reload.yaml",'w') as f:
    f.write(reload_config)

In [ ]:
# Train continued
!cd joeynmt; python3 -m joeynmt train configs/k5/transformer_reverse_ensw3_comet_reload.yaml

2022-07-01 21:19:40,985 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-07-01 21:19:41,913 - INFO - joeynmt.data - Loading training data...
2022-07-01 21:19:50,513 - INFO - joeynmt.data - Building vocabulary...
2022-07-01 21:19:52,063 - INFO - joeynmt.data - Loading dev data...
2022-07-01 21:19:53,743 - INFO - joeynmt.data - Loading test data...
2022-07-01 21:19:55,648 - INFO - joeynmt.data - Data loaded.
2022-07-01 21:19:55,648 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-07-01 21:19:55,853 - INFO - joeynmt.model - Enc-dec model built.
2022-07-01 21:19:59,790 - INFO - numexpr.utils - NumExpr defaulting to 2 threads.
2022-07-01 21:20:00,539 - INFO - joeynmt.training - Total params: 12132096
2022-07-01 21:20:04,011 - INFO - joeynmt.training - Loading model from /content/gdrive/Shareddrives/Low_Budget_MT/joeynmt/models/k5/transformer_reverse_ensw3_comet/45000.ckpt
2022-07-01 21:20:07,862 - INFO - joeynmt.helpers -                           cfg.name : t

## Iteration 4

In [ ]:
comet_data_load('swtrain.csv', 'sw', 'comet','k5', '4')

/content/gdrive/Shareddrives/Low_Budget_MT
data/sw
/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k5/comet
                                       source_sentence  \
456  Non executive-directors are paid a monthly fee...   

                                       target_sentence    scores  
456  Wakurugenzi wasio na mamlaka wanalipwa kila mw...  0.035145  
(5000, 3)


In [ ]:
split_srctgt('/data/sw/k5/comet/comet_train.csv','en', 'sw', 'comet','k5', '4')

(45000, 3)


In [ ]:
generating_BPE('en', 'sw', 'comet', 'k5','4')

### Training $M$

In [ ]:
# Swahili to English
run_model('sw', 'sw','en','transformer_reverse_ensw4_comet','comet','k5','4')
! cd joeynmt; python3 -m joeynmt train configs/k5/transformer_reverse_ensw4_comet.yaml

2022-07-02 15:18:42,638 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-07-02 15:18:43,097 - INFO - joeynmt.data - Loading training data...
2022-07-02 15:18:44,708 - INFO - joeynmt.data - Building vocabulary...
2022-07-02 15:18:45,170 - INFO - joeynmt.data - Loading dev data...
2022-07-02 15:18:45,184 - INFO - joeynmt.data - Loading test data...
2022-07-02 15:18:45,362 - INFO - joeynmt.data - Data loaded.
2022-07-02 15:18:45,362 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-07-02 15:18:45,581 - INFO - joeynmt.model - Enc-dec model built.
2022-07-02 15:18:49,828 - INFO - numexpr.utils - NumExpr defaulting to 2 threads.
2022-07-02 15:18:50,650 - INFO - joeynmt.training - Total params: 12132864
2022-07-02 15:18:54,364 - INFO - joeynmt.helpers -                           cfg.name : transformer_reverse_ensw4_comet
2022-07-02 15:18:54,364 - INFO - joeynmt.helpers -                       cfg.data.src : sw
2022-07-02 15:18:54,364 - INFO - joeynmt.helpers -   

## Iteration 5

In [ ]:
comet_data_load('swtrain.csv', 'sw', 'comet','k5', '5')

/content/gdrive/Shareddrives/Low_Budget_MT
data/sw
/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k5/comet
                                      source_sentence  \
10  In order to become a regional bank, the Board ...   

                                      target_sentence    scores  
10  Ili tuwe benki ya kanda, Halmashauri iliidhini...  0.041201  
(5000, 3)


In [ ]:
split_srctgt('/data/sw/k5/comet/comet_train.csv','en', 'sw', 'comet','k5', '5')

(50000, 3)


In [ ]:
generating_BPE('en', 'sw', 'comet', 'k5','5')

### Training $M$

In [ ]:
# Swahili to English
run_model('sw', 'sw','en','transformer_reverse_ensw5_comet','comet','k5','5')
! cd joeynmt; python3 -m joeynmt train configs/k5/transformer_reverse_ensw5_comet.yaml

2022-07-03 18:06:11,174 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-07-03 18:06:11,929 - INFO - joeynmt.data - Loading training data...
2022-07-03 18:06:12,650 - INFO - joeynmt.data - Building vocabulary...
2022-07-03 18:06:12,941 - INFO - joeynmt.data - Loading dev data...
2022-07-03 18:06:12,955 - INFO - joeynmt.data - Loading test data...
2022-07-03 18:06:13,319 - INFO - joeynmt.data - Data loaded.
2022-07-03 18:06:13,319 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-07-03 18:06:13,527 - INFO - joeynmt.model - Enc-dec model built.
2022-07-03 18:06:17,825 - INFO - numexpr.utils - NumExpr defaulting to 2 threads.
2022-07-03 18:06:18,631 - INFO - joeynmt.training - Total params: 12133120
2022-07-03 18:06:22,181 - INFO - joeynmt.helpers -                           cfg.name : transformer_reverse_ensw5_comet
2022-07-03 18:06:22,181 - INFO - joeynmt.helpers -                       cfg.data.src : sw
2022-07-03 18:06:22,182 - INFO - joeynmt.helpers -   

In [ ]:
!cd joeynmt; python -m joeynmt test 'models/k5/transformer_reverse_ensw5_comet/config.yaml'

2022-07-05 22:04:29,742 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-07-05 22:04:30,183 - INFO - joeynmt.data - Building vocabulary...
2022-07-05 22:04:31,656 - INFO - joeynmt.data - Loading dev data...
2022-07-05 22:04:32,178 - INFO - joeynmt.data - Loading test data...
2022-07-05 22:04:33,015 - INFO - joeynmt.data - Data loaded.
2022-07-05 22:04:33,083 - INFO - joeynmt.prediction - Process device: cuda, n_gpu: 1, batch_size per device: 3600
2022-07-05 22:04:33,083 - INFO - joeynmt.prediction - Loading model from models/k5/transformer_reverse_ensw5_comet/58800.ckpt
2022-07-05 22:04:39,081 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-07-05 22:04:39,276 - INFO - joeynmt.model - Enc-dec model built.
2022-07-05 22:04:39,340 - INFO - joeynmt.prediction - Decoding on dev set (/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k5/comet/5/dev.bpe.en)...
2022-07-05 22:05:11,052 - INFO - joeynmt.prediction -  dev bleu[13a]:  28.31 [Beam search decoding wit

## Iteration 6

In [ ]:
comet_data_load('swtrain.csv', 'sw', 'comet','k5', '6')

/content/gdrive/Shareddrives/Low_Budget_MT
data/sw
/content/gdrive/Shareddrives/Low_Budget_MT/data/sw/k5/comet
                                       source_sentence  \
814  And David commanded to gather together the soj...   

                                       target_sentence    scores  
814  Basi Daudi akaamuru wakusanyike wageni walioku...  0.046334  
(5000, 3)


In [ ]:
split_srctgt('/data/sw/k5/comet/comet_train.csv','en', 'sw', 'comet','k5', '6')

(55000, 3)


In [ ]:
generating_BPE('en', 'sw', 'comet', 'k5','6')

### Training $M$

In [ ]:
# Swahili to English
run_model('sw', 'sw','en','transformer_reverse_ensw6_comet','comet','k5','6')
! cd joeynmt; python3 -m joeynmt train configs/k5/transformer_reverse_ensw6_comet.yaml

2022-07-06 07:46:31,465 - INFO - root - Hello! This is Joey-NMT (version 1.5.1).
2022-07-06 07:46:32,004 - INFO - joeynmt.data - Loading training data...
2022-07-06 07:46:32,752 - INFO - joeynmt.data - Building vocabulary...
2022-07-06 07:46:33,036 - INFO - joeynmt.data - Loading dev data...
2022-07-06 07:46:33,056 - INFO - joeynmt.data - Loading test data...
2022-07-06 07:46:33,386 - INFO - joeynmt.data - Data loaded.
2022-07-06 07:46:33,387 - INFO - joeynmt.model - Building an encoder-decoder model...
2022-07-06 07:46:33,602 - INFO - joeynmt.model - Enc-dec model built.
2022-07-06 07:46:37,887 - INFO - numexpr.utils - NumExpr defaulting to 2 threads.
2022-07-06 07:46:38,365 - INFO - joeynmt.training - Total params: 12133888
2022-07-06 07:46:41,943 - INFO - joeynmt.helpers -                           cfg.name : transformer_reverse_ensw6_comet
2022-07-06 07:46:41,943 - INFO - joeynmt.helpers -                       cfg.data.src : sw
2022-07-06 07:46:41,943 - INFO - joeynmt.helpers -   